# **Analyse 2-2**

## Strategie & Fokus

- Versuche Clustering bzw. Zusammenfassung von Begriffen (z.B. Prüfung, Prüfen, Überprüfung)
- Orientierung an Häufigkeitsverteilung: häufigere Begriffe zuerst analysieren

---

# Merkmal 1: Clustering von Vorgangsbeschreibungen

## Recherche
[Textmining HS Hannover](https://textmining.wp.hs-hannover.de/Preprocessing.html)

### Allgemeine Zergliederung der Einzelbeschreibungen

- Text in Sätze
- Sätze in Wörter
- Wörter in Grundform:
    - Lemma: Die Form des Wortes, wie sie in einem Wörterbuch steht. Z.B.: Haus, laufen, begründen
    - Stamm: Das Wort ohne Flexionsendungen (Prefixe und Suffixe). Z.B.: Haus, lauf, begründ
    - Wurzel: Kern des Wortes, von dem das Wort ggf. durch Derivation abgeleitet wurde. Z.B.: Haus, lauf, Grund
- Wortartbestimmung
    - klassische Part-of-Speech-Erkennung (herkömmliche Wortart)
    - Named Entity Recognition (NER) (Eigennamen)
        - Bsp. spaCy: Person, Ort, Organisation, Verschiedenes

#### Semantik

- Wörter innerhalb eines Satzes größere Zusammenhänge als außerhalb

### Pakete

- Englisch: 
    - [NLTK](https://www.nltk.org/)
- Deutsch:
    - [HanTa - The Hanover Tagger](https://github.com/wartaal/HanTa/tree/master)
    - [TreeTagger](https://www.cis.uni-muenchen.de/~schmid/tools/TreeTagger/)
        - [Python Wrapper](https://treetaggerwrapper.readthedocs.io/en/latest/)
    - [spaCy](https://spacy.io/)
        - [Beispiel 1](https://www.trinnovative.de/blog/2020-09-08-natural-language-processing-mit-spacy.html)

21.02.:
- Überarbeitung RegEx-Filterung
- Verbesserung Duplikatefindung über Ähnlichkeit

## Analyse

In [339]:
import numpy as np
import pandas as pd
from pandas import DataFrame, Series
import spacy
from spacy.lang.de import German as GermanSpacyModel
import sentence_transformers
from sentence_transformers import SentenceTransformer
from collections import Counter
from itertools import combinations
from dateutil.parser import parse
import re
from spellchecker import SpellChecker

import matplotlib.pyplot as plt
import seaborn as sns

import logging
import sys
import pickle

LOGGING_LEVEL = 'INFO'
logging.basicConfig(level=LOGGING_LEVEL, stream=sys.stdout)
logger = logging.getLogger('base')

In [340]:
def save_pickle(obj, path):
    with open(path, 'wb') as file:
        pickle.dump(obj, file, protocol=pickle.HIGHEST_PROTOCOL)
        
def load_pickle(path):
    with open(path, 'rb') as file:
        obj = pickle.load(file)
    return obj

In [341]:
sns.set()
LOAD_CALC_FILES = False

DESC_BLACKLIST = set(['-'])
"""
GENERAL_BLACKLIST = set([
    'herr', 'hr.', 'förster', 'graf', 'stöppel', 
    'stab', 'kw', 'h.', 'koch', 'heininger', '.',
    'schwab', 'm.', 'wenninger', '-', '--',
])
"""

GENERAL_BLACKLIST = set([
    'herr', 'hr.' 'kw', 'h.', '.',
    'm.', '-', '--', 'dr.', 'dr',
])

#GENERAL_BLACKLIST = set()
#POS_of_interest = set(['NOUN', 'PROPN', 'ADJ', 'VERB', 'AUX'])
POS_of_interest = set(['NOUN', 'ADJ', 'VERB', 'AUX'])
TAG_of_interest = set(['ADJD'])

In [388]:
# load language model
# transformer model without vector embeddings
# can not be used to calculate similarities
# using sentence transformers instead
nlp = spacy.load('de_dep_news_trf')
#nlp = spacy.load('de_core_news_lg')

RuntimeError: Error(s) in loading state_dict for BertModel:
	Unexpected key(s) in state_dict: "embeddings.position_ids". 

In [343]:
model_stfr = SentenceTransformer('sentence-transformers/all-mpnet-base-v2')

INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: sentence-transformers/all-mpnet-base-v2
INFO:sentence_transformers.SentenceTransformer:Use pytorch device_name: cpu


In [344]:
# load dataset
FILE_PATH = '01_2_Rohdaten_neu/Export4.csv'
date_cols = ['VorgangsDatum', 'ErledigungsDatum', 'Arbeitsbeginn', 'ErstellungsDatum']
raw = pd.read_csv(filepath_or_buffer=FILE_PATH, sep=';', encoding='cp1252', parse_dates=date_cols, dayfirst=True)
raw.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 129020 entries, 0 to 129019
Data columns (total 20 columns):
 #   Column                   Non-Null Count   Dtype         
---  ------                   --------------   -----         
 0   VorgangsID               129020 non-null  int64         
 1   ObjektID                 129020 non-null  int64         
 2   HObjektText              129003 non-null  object        
 3   ObjektArtID              129020 non-null  int64         
 4   ObjektArtText            128372 non-null  object        
 5   VorgangsTypID            129020 non-null  int64         
 6   VorgangsTypName          129020 non-null  object        
 7   VorgangsDatum            129020 non-null  datetime64[ns]
 8   VorgangsStatusId         129020 non-null  int64         
 9   VorgangsPrioritaet       129020 non-null  int64         
 10  VorgangsBeschreibung     124087 non-null  object        
 11  VorgangsOrt              507 non-null     object        
 12  VorgangsArtText 

In [345]:
raw.head()

VorgangsID  ObjektID                                  HObjektText  \
0          11       114  427 C , Webmaschine, DL 280 EMS Breite 280    
1          17       124  621 C , Webmaschine, DL 280 EMS Breite 280    
2          53       244               285 C, Webmaschine, SG 220 EMS   
3          58       257                 107, Webmaschine, OM 220 EOS   
4          81       138                     00138, Schärmaschine 9,    

   ObjektArtID        ObjektArtText  VorgangsTypID            VorgangsTypName  \
0            3     Luft-Webmaschine              3  Reparaturauftrag (Portal)   
1            3     Luft-Webmaschine              3  Reparaturauftrag (Portal)   
2            5  Greifer-Webmaschine              3  Reparaturauftrag (Portal)   
3            3     Luft-Webmaschine              3  Reparaturauftrag (Portal)   
4           16        Schärmaschine              3  Reparaturauftrag (Portal)   

  VorgangsDatum  VorgangsStatusId  VorgangsPrioritaet  \
0    2019-03-06                 4                   0   
1    2019-03-11                 5                   0   
2    2019-03-19                 5                   0   
3    2019-03-21                 5                   0   
4    2019-03-25                 5                   0   

                       VorgangsBeschreibung VorgangsOrt  \
0                                       NaN         NaN   
1                                       NaN         NaN   
2                         Kupplung schleift         NaN   
3             Gegengewicht wieder anbringen         NaN   
4  da ist etwas gebrochen. (Herr Heininger)         NaN   

                                     VorgangsArtText ErledigungsDatum  \
0                                    Kettbaum kaputt       2019-03-06   
1                                            asgasdg       2019-03-11   
2                                    Kupplung defekt       2019-03-20   
3         Gegengewicht an der Webmaschine abgefallen       2019-03-21   
4  zentrale Bremsenverstellung linke Gatterseite ...       2019-03-25   

  ErledigungsArtText                            ErledigungsBeschreibung  \
0                NaN                                                NaN   
1                NaN                                                NaN   
2      Reparatur UTT                                                NaN   
3      Reparatur UTT  Schraube ausgebohrt\nGegengewicht wieder angeb...   
4      Reparatur UTT  Bolzen gebrochen. Bolzen neu angefertig und di...   

  MPMelderArbeitsplatz MPAbteilungBezeichnung Arbeitsbeginn ErstellungsDatum  
0              Weberei                Weberei           NaT       2019-03-06  
1     Elektrowerkstatt       Elektrowerkstatt           NaT       2019-03-11  
2              Weberei                Weberei           NaT       2019-03-19  
3              Weberei                Weberei    2019-03-21       2019-03-21  
4              Vorwerk                Vorwerk    2019-03-25       2019-03-25

In [346]:
print(f"Anzahl Features: {len(raw.columns)}")

Anzahl Features: 20


**Neue Features gegenüber letzter Analyse:**
- ``ObjektArtID``
- ``ObjektArtText``
- ``VorgangsTypName``

### Duplikate

In [347]:
duplicates_filt = raw.duplicated()

In [348]:
print(f"Anzahl Duplikate: {duplicates_filt.sum()}")

Anzahl Duplikate: 84


In [349]:
filt_data = raw[duplicates_filt]
uni_obj_id_dupl = filt_data['ObjektID'].unique()

In [350]:
print(f"Anzahl einzigartiger Objekt-IDs unter Duplikaten: {len(uni_obj_id_dupl)}")

Anzahl einzigartiger Objekt-IDs unter Duplikaten: 47


In [351]:
wo_duplicates = raw.drop_duplicates(ignore_index=True)
wo_duplicates.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 128936 entries, 0 to 128935
Data columns (total 20 columns):
 #   Column                   Non-Null Count   Dtype         
---  ------                   --------------   -----         
 0   VorgangsID               128936 non-null  int64         
 1   ObjektID                 128936 non-null  int64         
 2   HObjektText              128920 non-null  object        
 3   ObjektArtID              128936 non-null  int64         
 4   ObjektArtText            128289 non-null  object        
 5   VorgangsTypID            128936 non-null  int64         
 6   VorgangsTypName          128936 non-null  object        
 7   VorgangsDatum            128936 non-null  datetime64[ns]
 8   VorgangsStatusId         128936 non-null  int64         
 9   VorgangsPrioritaet       128936 non-null  int64         
 10  VorgangsBeschreibung     124008 non-null  object        
 11  VorgangsOrt              507 non-null     object        
 12  VorgangsArtText 

### ``VorgangsBeschreibung``

#### **NA vals und Duplikate**

String-Bereinigung

In [352]:
SPECIAL_CHARS = set(['&', '$', '%', '§', '/', '(', ')', '_', 
                     '+', '–', '--', '<', '>', '´',
])

In [353]:
def clean_string_slim(string: str) -> str:
    # remove special chars
    pattern = r'[\t\n\r\f\v]'
    string = re.sub(pattern, ' ', string)
    # remove whitespaces at the beginning and the end
    string = string.strip()
    
    return string

def clean_string(string: str) -> str:
    #num_reps = 5
    
    # remove special chars
    pattern = r'[\t\n\r\f\v]'
    string = re.sub(pattern, ' ', string)
    # remove dates
    pattern = r'[\d]{1,4}[.:][\d]{1,4}[.:][\d]{1,4}'
    string = re.sub(pattern, '', string)
    # remove times
    pattern = r'[\d]{1,2}[:][\d]{1,2}[:][\d]{0,2}'
    string = re.sub(pattern, '', string)
    # remove all chars despite punctuation and alphanumeric ones
    pattern = r'[^ \w.,;:\-äöüÄÖÜ]+'
    string = re.sub(pattern, '', string)
    # remove - where it is used as em dash
    pattern = r'[\W]+-[\W]+'
    string = re.sub(pattern, ' ', string)
    # remove whitespaces in front of punctuation
    pattern = r'[ ]+([;,.:])'
    string = re.sub(pattern, r'\1', string)
    # remove multiple whitespaces
    pattern = r'[ ]+'
    string = re.sub(pattern, ' ', string)
    # remove whitespaces at the beginning and the end
    string = string.strip()
    
    #while num_reps != 0:
        #string = string.replace('\n', ' ')
        #string = string.replace('\t', ' ')
        #string = string.replace('  ', ' ')
        #string = string.replace('   ', ' ')
    #string = string.replace(' - ', ' ')
    """
    for char in SPECIAL_CHARS:
        string = string.replace(char, '')
        
        #num_reps -= 1
    
    # remove spaces at the beginning and the end
    string = string.strip()
    """
    
    return string

In [354]:
base = wo_duplicates.copy()
base = base.dropna(axis=0, subset='VorgangsBeschreibung')
# preprocessing
#base['VorgangsBeschreibung'] = base['VorgangsBeschreibung'].map(clean_string)
base['VorgangsBeschreibung'] = base['VorgangsBeschreibung'].map(clean_string_slim)

In [355]:
base

VorgangsID  ObjektID                             HObjektText  \
2               53       244          285 C, Webmaschine, SG 220 EMS   
3               58       257            107, Webmaschine, OM 220 EOS   
4               81       138                00138, Schärmaschine 9,    
5               82         0                    Warenschau allgemein   
6               76         0                          Neben der Türe   
...            ...       ...                                     ...   
128931      518956      1708  01708, Betriebsfahrräder Schlosserei,    
128932      275123      1654  WEBEREI ALLGEMEIN, Weberei allgemein,    
128933      275125      1795              A054.S, Jacquardmaschine,    
128934      275188         1            00001, Ausrüstungsanlage 1,    
128935      275219       326                   B38, Niederhubwagen,    

        ObjektArtID                                ObjektArtText  \
2                 5                          Greifer-Webmaschine   
3                 3                             Luft-Webmaschine   
4                16                                Schärmaschine   
5                 0                                          NaN   
6                 0                                          NaN   
...             ...                                          ...   
128931           57                      Interne Wartungsobjekte   
128932           90                                UTT allgemein   
128933           24                     Stäubli-Jacquardmaschine   
128934            1                                Waschmaschine   
128935           32  Flurförderzeuge / Putzmaschine / Rasenmäher   

        VorgangsTypID            VorgangsTypName VorgangsDatum  \
2                   3  Reparaturauftrag (Portal)    2019-03-19   
3                   3  Reparaturauftrag (Portal)    2019-03-21   
4                   3  Reparaturauftrag (Portal)    2019-03-25   
5                   3  Reparaturauftrag (Portal)    2019-03-25   
6                   3  Reparaturauftrag (Portal)    2019-03-22   
...               ...                        ...           ...   
128931              1                    Wartung    2023-06-19   
128932              3  Reparaturauftrag (Portal)    2022-09-29   
128933              3  Reparaturauftrag (Portal)    2022-09-30   
128934              3  Reparaturauftrag (Portal)    2022-09-30   
128935              3  Reparaturauftrag (Portal)    2022-10-03   

        VorgangsStatusId  VorgangsPrioritaet  \
2                      5                   0   
3                      5                   0   
4                      5                   0   
5                      5                   0   
6                      5                   0   
...                  ...                 ...   
128931                 5                   0   
128932                 5                   0   
128933                 5                   0   
128934                 5                   1   
128935                 5                   0   

                                     VorgangsBeschreibung  \
2                                       Kupplung schleift   
3                           Gegengewicht wieder anbringen   
4                da ist etwas gebrochen. (Herr Heininger)   
5                        Klappbügel Portalkran H31 defekt   
6                                    Schraube nix mer gut   
...                                                   ...   
128931  2-wöchige Reinigung & Sichtkontrolle (Technisc...   
128932       Adapter entfernen und Gewinde nachschneiden.   
128933  Alle 4 Schrauben und teile der Kettbaumlagerun...   
128934            Walzenlager WK 6 überprüfen/auswechseln   
128935  Befestigung Deckel für Batteriefach defekt    ...   

                 VorgangsOrt  \
2                        NaN   
3                        NaN   
4                        NaN   
5       Warenschau allgemein   
6             Neben der Türe   
...                      ...   

In [356]:
descriptions = base['VorgangsBeschreibung']
print(f"Einträge: {len(descriptions)}")

Einträge: 124008


In [357]:
num_dupl_descr = descriptions.duplicated().sum()
uni_descr = descriptions.unique()
num_uni_descr = len(uni_descr)

print(f"Anzahl Duplikate Vorgangsbeschreibungen: {num_dupl_descr}")
print(f"Anzahl einzigartiger Vorgangsbeschreibungen: {num_uni_descr}")
print(f"Anteil einzigartiger Vorgangsbeschreibungen: {num_uni_descr / len(descriptions) * 100:.2f} %")

Anzahl Duplikate Vorgangsbeschreibungen: 117208
Anzahl einzigartiger Vorgangsbeschreibungen: 6800
Anteil einzigartiger Vorgangsbeschreibungen: 5.48 %


In [358]:
if not LOAD_CALC_FILES:
    cols = ['descr', 'len', 'num_occur', 'assoc_obj_ids', 'num_assoc_obj_ids']
    descr_df = pd.DataFrame(columns=cols)
    max_val = 0
    text = None
    index = 0


    for idx, description in enumerate(uni_descr):
        len_descr = len(description)
        filt = base['VorgangsBeschreibung'] == description
        temp = base[filt]
        assoc_obj_ids = temp['ObjektID'].unique()
        assoc_obj_ids = np.sort(assoc_obj_ids, kind='stable')
        num_assoc_obj_ids = len(assoc_obj_ids)
        num_dupl = filt.sum()
        
        conc_df = pd.DataFrame(data=[[
                                description,
                                len_descr,
                                num_dupl,
                                assoc_obj_ids,
                                num_assoc_obj_ids
                            ]], columns=cols)
        
        descr_df = pd.concat([descr_df, conc_df], ignore_index=True)
        
        if num_dupl > max_val:
            max_val = num_dupl
            index = idx
            text = description
            
    temp1 = descr_df.sort_values(by='num_occur', ascending=False)

In [359]:
temp1

descr  len num_occur  \
162   Tägliche Wartungstätigkeiten nach Vorgabe des ...   66     92592   
33              Wöchentliche Sichtkontrolle / Reinigung   39      1654   
131               Tägliche Überprüfung der Ölabscheider   37      1616   
160               Wöchentliche Kontrolle der WC-Anlagen   37      1265   
140        Halbjährliche Kontrolle des Stabbreithalters   44       687   
...                                                 ...  ...       ...   
2679  Zahnräder der Laufkatze verschlissen Ersatztei...  170         1   
2678   Bitte 8 Scheiben nach Muster anfertigen.  Danke.   48         1   
2677  Schalter für Bühne Schwenken abgerissen, bitte...  126         1   
2676                                  Docke angefahren!   17         1   
6799  Befestigung Deckel für Batteriefach defekt    ...  107         1   

                                          assoc_obj_ids num_assoc_obj_ids  
162   [0, 17, 41, 42, 43, 44, 45, 46, 47, 51, 52, 53...               206  
33    [301, 304, 305, 313, 314, 331, 332, 510, 511, ...                18  
131                                [0, 970, 2134, 2137]                 4  
160   [1352, 1353, 1354, 1684, 1685, 1686, 1687, 168...                11  
140   [51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 6...               166  
...                                                 ...               ...  
2679                                              [415]                 1  
2678                                              [140]                 1  
2677                                              [323]                 1  
2676                                              [176]                 1  
6799                                              [326]                 1  

[6800 rows x 5 columns]

In [360]:
temp1.iloc[0,0]

'Tägliche Wartungstätigkeiten nach Vorgabe des Maschinenherstellers'

In [361]:
temp1.iloc[1,0]

'Wöchentliche Sichtkontrolle / Reinigung'

**Cosine Similarity**

In [362]:
# eliminate descriptions with less than 6 symbols
subset_data = temp1.loc[temp1['len'] > 5, 'descr'].copy()
subset_data = subset_data.iloc[0:100]

- Wie geht man mit unbekannten Wörtern um?

In [363]:
# build mapping of embeddings for given model
def build_embedding_map(
    data: Series,
    model: GermanSpacyModel | SentenceTransformer,
) -> dict[int, tuple['Embedding',str]]:
    # dictionary with embeddings
    embeddings: dict[int, tuple['Embedding',str]] = dict()
    is_spacy = False
    is_STRF = False
    
    if isinstance(model, spacy.lang.de.German):
        is_spacy = True
    elif isinstance(model, SentenceTransformer):
        is_STRF = True
        
    if not any((is_spacy, is_STRF)):
        raise NotImplementedError("Model type unknown")
        
    for (idx, text) in subset_data.items():
        
        if is_spacy:
            embd = model(text)
            embeddings[idx] = (embd, text)
            # check for empty vectors
            if not doc.vector_norm:
                print('--- Unknown Words ---')
                print(f'{embd.text=} has no vector')
        elif is_STRF:
            embd = model.encode(text, show_progress_bar=False, normalize_embeddings=False)
            embeddings[idx] = (embd, text)
    
    return embeddings, (is_spacy, is_STRF)

# build similarity matrix out of embeddings
def build_cosSim_matrix(
    data: Series,
    model: GermanSpacyModel | SentenceTransformer,
) -> DataFrame:
    # build empty matrix
    df_index = data.index
    cosineSim_idx_matrix = pd.DataFrame(data=0., columns=df_index, 
                                    index=df_index, dtype=np.float32)
    
    # obtain embeddings based on used model
    embds, (is_spacy, is_STRF) = build_embedding_map(
        data=data,
        model=model
    )
    
    # apply index based mapping for efficient handling of large texts
    combs = combinations(df_index, 2)
    
    for (idx1, idx2) in combs:
        #print(f"{idx1=}, {idx2=}")
        embd1 = embds[idx1][0]
        embd2 = embds[idx2][0]
        
        # calculate similarity based on model type
        if is_spacy:
            cosSim = embd1.similarity(embd2)
        elif is_STRF:
            cosSim = sentence_transformers.util.cos_sim(embd1, embd2)
            cosSim = cosSim.item()
        
        cosineSim_idx_matrix.at[idx1, idx2] = cosSim
        
    return cosineSim_idx_matrix, embds

In [364]:
cosineSim_idx_matrix, embds = build_cosSim_matrix(
    data=subset_data,
    model=model_stfr,
)

In [365]:
cosineSim_idx_matrix

162       33        131       160       140       1780      332   \
162    0.0  0.441387  0.409547  0.307963  0.324018  0.506761  0.475413   
33     0.0  0.000000  0.298110  0.372992  0.412453  0.374439  0.423904   
131    0.0  0.000000  0.000000  0.305271  0.390110  0.406878  0.390903   
160    0.0  0.000000  0.000000  0.000000  0.294035  0.293377  0.457293   
140    0.0  0.000000  0.000000  0.000000  0.000000  0.353114  0.368328   
...    ...       ...       ...       ...       ...       ...       ...   
47     0.0  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2951   0.0  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
185    0.0  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
566    0.0  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
40     0.0  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   

          104       157       558   ...      180       3485      2255  \
162   0.475614  0.491961  0.472069  ...  0.306548  0.318907  0.329199   
33    0.416100  0.717584  0.422673  ...  0.317514  0.321114  0.367475   
131   0.417179  0.324945  0.392856  ...  0.387864  0.386872  0.466728   
160   0.251860  0.327785  0.456575  ...  0.291295  0.356851  0.326423   
140   0.319977  0.402378  0.368687  ...  0.328528  0.298065  0.515159   
...        ...       ...       ...  ...       ...       ...       ...   
47    0.000000  0.000000  0.000000  ...  0.000000  0.000000  0.000000   
2951  0.000000  0.000000  0.000000  ...  0.000000  0.000000  0.000000   
185   0.000000  0.000000  0.000000  ...  0.000000  0.000000  0.000000   
566   0.000000  0.000000  0.000000  ...  0.000000  0.000000  0.000000   
40    0.000000  0.000000  0.000000  ...  0.000000  0.000000  0.000000   

          81        360       47        2951      185       566       40    
162   0.296131  0.283268  0.442444  0.129318  0.425916  0.432691  0.356977  
33    0.327464  0.228003  0.351899  0.245888  0.383551  0.384033  0.746593  
131   0.368427  0.297099  0.393476  0.080983  0.344004  0.346553  0.300196  
160   0.340315  0.241496  0.363125  0.205827  0.350013  0.322723  0.233216  
140   0.315984  0.240238  0.406395  0.164005  0.405763  0.403172  0.381799  
...        ...       ...       ...       ...       ...       ...       ...  
47    0.000000  0.000000  0.000000  0.119025  0.294950  0.281203  0.317069  
2951  0.000000  0.000000  0.000000  0.000000  0.359434  0.353695  0.223206  
185   0.000000  0.000000  0.000000  0.000000  0.000000  0.978342  0.411086  
566   0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.404999  
40    0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  

[100 rows x 100 columns]

In [366]:
# obtain index pairs with cosine similarity 
# greater than or equal to given threshold value

def filt_thresh_cosSim_matrix(
    threshold: float,
    cosineSim_idx_matrix: DataFrame,
):
    cosineSim_filt = cosineSim_idx_matrix.where(cosineSim_idx_matrix >= threshold).stack()
    
    return cosineSim_filt

def list_cosSim_dupl_candidates(
    cosineSim_filt: Series,
    embeddings: dict[int, tuple['Embedding',str]],
):
    # compare found duplicates
    columns = ['idx1', 'text1', 'idx2', 'text2', 'score']
    df_candidates = pd.DataFrame(columns=columns)
    
    index_pairs = list()

    for ((idx1, idx2), score) in cosineSim_filt.items():
        # get text content from embedding as second tuple entry
        content = [[
            idx1,
            embeddings[idx1][1],
            idx2,
            embeddings[idx2][1],
            score,
        ]]
        df_conc = pd.DataFrame(columns=columns, data=content)
        
        df_candidates = pd.concat([df_candidates, df_conc])
        index_pairs.append((idx1, idx2))
    
    return df_candidates, index_pairs

def choose_cosSim_dupl_candidates(
    cosineSim_filt: Series,
    embeddings: dict[int, tuple['Embedding',str]],
) -> tuple[DataFrame, list[tuple['Index', 'Index']]]:
    # compare found duplicates
    columns = ['idx1', 'text1', 'idx2', 'text2', 'score']
    df_candidates = pd.DataFrame(columns=columns)
    
    index_pairs = list()

    for ((idx1, idx2), score) in cosineSim_filt.items():
        # get texts for comparison
        text1 = embeddings[idx1][1]
        text2 = embeddings[idx2][1]
        # get decision
        print('---------- New Decision ----------')
        print('text1:\n', text1, '\n', flush=True)
        print('text2:\n', text2, '\n', flush=True)
        decision = input('Please enter >>y<< if this is a duplicate, else hit enter:')
        
        if not decision == 'y':
            continue
        
        # get text content from embedding as second tuple entry
        content = [[
            idx1,
            text1,
            idx2,
            text2,
            score,
        ]]
        df_conc = pd.DataFrame(columns=columns, data=content)
        
        df_candidates = pd.concat([df_candidates, df_conc])
        index_pairs.append((idx1, idx2))
    
    return df_candidates, index_pairs

In [367]:
SIMILARITY_THRESHOLD = 0.8

cosineSim_filt = filt_thresh_cosSim_matrix(
    threshold=SIMILARITY_THRESHOLD,
    cosineSim_idx_matrix=cosineSim_idx_matrix,
)
cosineSim_filt

33    176     0.921449
      247     0.903092
332   558     0.987194
157   247     0.812700
176   247     0.816763
34    63      0.952310
477   247     0.831053
111   360     0.991955
53    56      0.866648
      15      0.871172
56    15      0.989507
84    191     0.999377
28    173     0.836900
184   40      0.959962
602   255     0.800500
29    78      0.939677
732   185     0.815442
136   174     0.943705
680   106     0.889502
6580  3371    0.866680
185   566     0.978342
dtype: float32

In [ ]:
cosSim_dupl_candidates, dupl_idx_pairs = list_cosSim_dupl_candidates(
    cosineSim_filt=cosineSim_filt,
    embeddings=embds,
)
# save results
SAVE_PATH_DUPL_CANDIDATES = (f'./Filterung_Duplikate/dupl_candidates_'
                             f'cosSim_thresh_{SIMILARITY_THRESHOLD}.xlsx')
#cosSim_dupl_candidates.to_excel(SAVE_PATH_DUPL_CANDIDATES)
cosSim_dupl_candidates

idx1                                              text1 idx2  \
0  332  Prüfung von:  - Scharniere - Dichtung - Schlie...  558   
0  111  Tägliche Interne Wartungstätigkeiten durch die...  360   
0   56  Vorgaben aus Brückner Wartungsplan (siehe Extr...   15   
0   84  Vorgabe aus Wartungsplan Firma Menzel (siehe V...  191   
0  185  Vorgabe aus Wartungsplan Firma Menzel (siehe V...  566   

                                               text2     score  
0  Monatliche Prüfung von:  - Scharniere - Dichtu...  0.987194  
0  Wöchentliche Interne Wartungstätigkeiten durch...  0.991955  
0  Vorgaben aus Brückner Wartungsplan  siehe Extr...  0.989507  
0  Vorgabe aus Wartungsplan Firma Menzel (siehe V...  0.999377  
0  Vorgabe aus Wartungsplan Firma Menzel (siehe V...  0.978342

**Nächste Schritte:**
- Grenz-Threshold finden, bei dem Duplikate gerade noch richtig erkannt werden

In [ ]:
thresholds = (0.75, 0.8, 0.85, 0.9, 0.93, 0.95, 0.96, 0.97, 0.98)

for thresh in thresholds:
    
    cosineSim_filt = filt_thresh_cosSim_matrix(
        threshold=thresh,
        cosineSim_idx_matrix=cosineSim_idx_matrix.copy(),
    )
    
    cosSim_dupl_candidates = list_cosSim_dupl_candidates(
        cosineSim_filt=cosineSim_filt,
        embeddings=embds,
    )
    
    # saving path
    saving_path = (f'./Filterung_Duplikate/dupl_candidates_'
                   f'cosSim_thresh_{thresh}_STFR.xlsx')
    
    cosSim_dupl_candidates.to_excel(saving_path)

**Ergebnisse:**
- kein allgemeiner Threshold ableitbar, nur grober Richtwert
- Paare mit geringerem Score stellenweise ähnlicher als die mit höherem Score
- finale Entscheidung für Duplikat händisch, da Kontextwissen trotzdem notwendig
- Arbeit mit ``temp1`` und merging von Einträgen

In [368]:
# manually decide if candidates are indeed duplicates

SKIP = True
if not SKIP:
    cosSim_dupl_candidates, dupl_idx_pairs = choose_cosSim_dupl_candidates(
        cosineSim_filt=cosineSim_filt,
        embeddings=embds,
    )

In [ ]:
#save_pickle(obj=dupl_idx_pairs, path='./Filterung_Duplikate/dupl_idx_pairs_Exp4.pkl')

In [369]:
dupl_idx_pairs = load_pickle(path='./Filterung_Duplikate/dupl_idx_pairs_Exp4.pkl')
dupl_idx_pairs

[(33, 176),
 (332, 558),
 (34, 63),
 (53, 56),
 (53, 15),
 (56, 15),
 (84, 191),
 (29, 78),
 (136, 174),
 (680, 106),
 (185, 566)]

In [433]:
temp2 = temp1.copy()

In [434]:
# merge duplicates

# to-do:
# merge: 'num_occur', 'assoc_obj_ids', 
# recalc: 'num_assoc_obj_ids'

for (i1, i2) in dupl_idx_pairs:
    
    # if an entry does not exist anymore, skip this pair
    if i1 not in temp2.index or i2 not in temp2.index:
        continue
    
    # merge num occur
    num_occur1 = temp2.at[i1, 'num_occur']
    num_occur2 = temp2.at[i2, 'num_occur']
    new_num_occur = num_occur1 + num_occur2

    # merge assoc obj ids
    assoc_ids1 = temp2.at[i1, 'assoc_obj_ids']
    assoc_ids2 = temp2.at[i2, 'assoc_obj_ids']
    new_assoc_ids = np.append(assoc_ids1, assoc_ids2)
    new_assoc_ids = np.unique(new_assoc_ids.flatten())

    # recalc num assoc obj ids
    new_num_assoc_obj_ids = len(new_assoc_ids)

    # write porperties to first entry
    temp2.at[i1, 'num_occur'] = new_num_occur
    temp2.at[i1, 'assoc_obj_ids'] = new_assoc_ids
    temp2.at[i1, 'num_assoc_obj_ids'] = new_num_assoc_obj_ids
    
    # drop second entry
    temp2 = temp2.drop(index=i2)

In [435]:
temp1

descr  len num_occur  \
162   Tägliche Wartungstätigkeiten nach Vorgabe des ...   66     92592   
33              Wöchentliche Sichtkontrolle / Reinigung   39      1654   
131               Tägliche Überprüfung der Ölabscheider   37      1616   
160               Wöchentliche Kontrolle der WC-Anlagen   37      1265   
140        Halbjährliche Kontrolle des Stabbreithalters   44       687   
...                                                 ...  ...       ...   
2679  Zahnräder der Laufkatze verschlissen Ersatztei...  170         1   
2678   Bitte 8 Scheiben nach Muster anfertigen.  Danke.   48         1   
2677  Schalter für Bühne Schwenken abgerissen, bitte...  126         1   
2676                                  Docke angefahren!   17         1   
6799  Befestigung Deckel für Batteriefach defekt    ...  107         1   

                                          assoc_obj_ids num_assoc_obj_ids  
162   [0, 17, 41, 42, 43, 44, 45, 46, 47, 51, 52, 53...               206  
33    [301, 304, 305, 313, 314, 331, 332, 510, 511, ...                18  
131                                [0, 970, 2134, 2137]                 4  
160   [1352, 1353, 1354, 1684, 1685, 1686, 1687, 168...                11  
140   [51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 6...               166  
...                                                 ...               ...  
2679                                              [415]                 1  
2678                                              [140]                 1  
2677                                              [323]                 1  
2676                                              [176]                 1  
6799                                              [326]                 1  

[6800 rows x 5 columns]

In [436]:
temp2['assoc_obj_ids'] = temp2['assoc_obj_ids'].map(lambda x: x.tolist())

In [437]:
temp2

descr  len num_occur  \
162   Tägliche Wartungstätigkeiten nach Vorgabe des ...   66     92592   
33              Wöchentliche Sichtkontrolle / Reinigung   39      2015   
131               Tägliche Überprüfung der Ölabscheider   37      1616   
160               Wöchentliche Kontrolle der WC-Anlagen   37      1265   
140        Halbjährliche Kontrolle des Stabbreithalters   44       687   
...                                                 ...  ...       ...   
2679  Zahnräder der Laufkatze verschlissen Ersatztei...  170         1   
2678   Bitte 8 Scheiben nach Muster anfertigen.  Danke.   48         1   
2677  Schalter für Bühne Schwenken abgerissen, bitte...  126         1   
2676                                  Docke angefahren!   17         1   
6799  Befestigung Deckel für Batteriefach defekt    ...  107         1   

                                          assoc_obj_ids num_assoc_obj_ids  
162   [0, 17, 41, 42, 43, 44, 45, 46, 47, 51, 52, 53...               206  
33    [301, 304, 305, 313, 314, 323, 329, 331, 332, ...                23  
131                                [0, 970, 2134, 2137]                 4  
160   [1352, 1353, 1354, 1684, 1685, 1686, 1687, 168...                11  
140   [51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 6...               166  
...                                                 ...               ...  
2679                                              [415]                 1  
2678                                              [140]                 1  
2677                                              [323]                 1  
2676                                              [176]                 1  
6799                                              [326]                 1  

[6790 rows x 5 columns]

In [438]:
LOAD_CALC_FILES = False

# save/load dataframe
#FILE_PATH = 'VorgangsBeschreibung_analyse_20240306.fth'
FILE_PATH = 'VorgangsBeschreibung_analyse_20240306.pkl'
if LOAD_CALC_FILES:
    temp1 = pd.read_feather(FILE_PATH)
    temp1 = temp1.set_index('index')
else:
    save_df = temp2.copy()
    #save_df = temp2.reset_index()
    #save_df.to_feather(FILE_PATH)
    #save_df.to_parquet(FILE_PATH)
    save_df.to_pickle(FILE_PATH)

- Handling von Rechtschreibfehlern (Hunspell über PyEnchant)
- Handling von Vector-Embeddings über Transformer-Modelle:
    - höhere Fehlertoleranz (Rechtschreibung, redundante oder unbedeutende Worte)
    - nicht angewiesen, dass jedes Wort im Vocabulary vorkommt (vgl. spaCy-Modell)
    - bei ersten Versuchen höhere Genauigkeit bei der Erkennung tatsächlicher Duplikate
- Nutzung Vector-Embeddings für Duplikatfindung

#### ---> Model Training: Data Set

In [27]:
# data for model training
data = temp1.iloc[50:300,0].to_list()
data = [e for e in data if e != '']

with open('spacy_train/training_data_2.txt','w', encoding='utf-8') as f:
    f.writelines("\n".join(data))

In [234]:
# save/load dataframe
FILE_PATH = 'VorgangsBeschreibung_analyse_1.fth'
if LOAD_CALC_FILES:
    temp1 = pd.read_feather(FILE_PATH)
    temp1 = temp1.set_index('index')
else:
    save_df = temp1.reset_index()
    save_df.to_feather(FILE_PATH)

#### spaCy

In [245]:
string = temp1.iloc[-2,0]
#string = temp1.iloc[0,0]
string

'Durchführung: Sollwert: 20 0,1g'

In [246]:
string = 'Ich spiele jeden Tag mit den Kindern im Garten. Das ist schön.'
string = 'Die Maschine XYZ ist aufgrund einer Störung im Druckluftsystem defekt.'
#string = 'The machine XYZ is broken because of a failure in the air pressure system.'
#string = 'Wir benötigen das Werkzeug von Herr Stöppel, um das derzeit abzuarbeiten.Dies wird durch Herrn Strebe getan.'

In [247]:
doc = nlp(string)

In [248]:
# simulate occurence counter
OCC_COUNTER = 10

In [249]:
SPELL_CHECK_NON_CHARS = set([' ', '.', ',', ';', ':', '-'])
CLEANING = True
#CLEANING = False

def pre_clean_word(string: str) -> str:
    
    pattern = r'[^A-Za-zäöüÄÖÜ]+'
    string = re.sub(pattern, '', string)
    """
    for char in SPELL_CHECK_NON_CHARS:
        string = string.replace(char, '')
    """
    
    return string

# https://stackoverflow.com/questions/25341945/check-if-string-has-date-any-format 
def is_str_date(string, fuzzy=False):
    
    try:
        parse(string, fuzzy=fuzzy)
        return True
    except ValueError:
        return False


def obtain_sub_tree(token):
    # check if token is a POS of interest
    descendants = list(token.subtree)
    descendants.remove(token)
    logger.debug(f'Token >>{token}<< has subtree >>{descendants}<<')
    return descendants


def add_children_descendants(
    parent,
    weight,
    connections,
    unique_tokens,
    children_sents,
    map_2_word: dict[str, str] | None = None,
):
    global CLEANING
    # add child as key
    if CLEANING:
        parent_lemma = pre_clean_word(string=parent.lemma_)
        
        # map words
        if word_2_map is not None:
            if parent_lemma.lower() in map_2_word:
                parent_lemma = map_2_word[parent_lemma.lower()]
                #logger.info(f"[SUCCESS] Mapped PARENT to {parent_lemma}")
        
        if parent_lemma != '':
            if (parent_lemma, parent.pos_) in connections:
                connections[(parent_lemma, parent.pos_)].append(children_sents)
                connections[(parent_lemma, parent.pos_)].append(children_sents)
                #connections[parent.lemma_].append([descendant.lemma_, descendant])
            else:
                # do not add auxiliary words
                if parent.pos_ != 'AUX':
                    unique_tokens.add(parent_lemma)
                connections[(parent_lemma, parent.pos_)] = list()
                connections[(parent_lemma, parent.pos_)].append(children_sents)
                #connections[parent.lemma_].append([descendant.lemma_, descendant])
    else:
        if (parent.lemma_, parent.pos_) in connections:
            connections[(parent.lemma_, parent.pos_)].append(children_sents)
            connections[(parent.lemma_, parent.pos_)].append(children_sents)
            #connections[parent.lemma_].append([descendant.lemma_, descendant])
        else:
            # do not add auxiliary words
            if parent.pos_ != 'AUX':
                unique_tokens.add(parent.lemma_)
            connections[(parent.lemma_, parent.pos_)] = list()
            connections[(parent.lemma_, parent.pos_)].append(children_sents)
            #connections[parent.lemma_].append([descendant.lemma_, descendant])


def obtain_descendant_info(
    doc,
    weight,
    POS_of_interest,
    TAG_of_interest,
    connections,
    unique_tokens,
    spell_check_candidates,
    spell_check_whitelist,
    spell_checker,
    corrections,
    map_2_word: dict[str, str] | None = None,
):
    global GENERAL_BLACKLIST
    global DESC_BLACKLIST
    global CLEANING
    
    # iterate over sentences
    for sent in doc.sents:
        # [REWORK] spell check list
        spell_check_words = list()
        
        # iterate over tokens in one sentence
        for token in sent:
            
            if not (token.pos_ in POS_of_interest or token.tag_ in TAG_of_interest):
                continue
            elif token.lemma_.lower() in GENERAL_BLACKLIST:
                logger.debug(f'Eliminated parent >>{token}<< because of blacklist')
                continue
            
            # [REWORK] spell check
            """
            if token.lemma_.lower() not in spell_check_whitelist:
                word = pre_clean_word(string=token.lemma_.lower())
                if word in corrections:
                    word = corrections[word]
                elif not word.isdigit():
                    spell_check_words.append(word)
            """
            
            descendants = obtain_sub_tree(token=token)
            
            # iterate over all children if there are any
            if descendants is not None:
                # list with all children in the current sentence
                children_sents = list()
                
                for child in descendants:
                    logger.debug(f'Token is >>{token}<< with child >>{child}<< and POS {child.pos_}')
                    
                    # elimnate cases of cross-references with verbs
                    if ((token.pos_ == 'AUX' or token.pos_ == 'VERB') and
                        (child.pos_ == 'AUX' or child.pos_ == 'VERB')):
                        continue
                    elif not (child.pos_ in POS_of_interest or child.tag_ in TAG_of_interest):
                        continue
                    elif child.lemma_.lower() in GENERAL_BLACKLIST:
                        logger.debug(f'Eliminated child >>{child}<< because of blacklist')
                        continue
                    
                    
                    if CLEANING:
                        child = pre_clean_word(string=child.lemma_)
                        if child == '':
                            continue
                        #child = pre_clean_word(string=child)
                        
                        if (child not in DESC_BLACKLIST and
                            not is_str_date(string=child)):
                            #not is_str_date(string=child.text)):
                            #children_sents.append((child.lemma_, weight))
                            
                            # map words
                            if map_2_word is not None:
                                if child.lower() in map_2_word:
                                    child = map_2_word[child.lower()]
                                    #logger.info(f"[SUCCESS] Mapped CHILD to {child}")
                            
                            children_sents.append((child, weight))
                        
                        #if child.lemma_ not in unique_tokens:
                        if child not in unique_tokens:
                            #unique_tokens.add(child.lemma_)
                            unique_tokens.add(child)
                            
                    else:
                        if (child.lemma_ not in DESC_BLACKLIST and
                            not is_str_date(string=child.text)):
                            children_sents.append((child.lemma_, weight))
                        
                        if child.lemma_ not in unique_tokens:
                            unique_tokens.add(child.lemma_)
                    
                    # [REWORK] spell check
                    """
                    if child.lemma_.lower() not in spell_check_whitelist:
                        word = pre_clean_word(string=child.lemma_.lower())
                        if word in corrections:
                            word = corrections[word]
                        elif not word.isdigit():
                            spell_check_words.append(word)
                    """
                
                # add list of children for current parent if not empty
                if children_sents:
                    
                    add_children_descendants(
                        parent=token,
                        weight=weight,
                        connections=connections,
                        unique_tokens=unique_tokens,
                        children_sents=children_sents,
                        map_2_word=map_2_word,
                    )
        
        misspelled_candidates = spell_checker.unknown(spell_check_words)
        spell_check_candidates.update(misspelled_candidates)

In [250]:
def obtain_adj_matrix(unique_tokens, connections):

    adj_mat = pd.DataFrame(
        data=0, 
        columns=list(unique_tokens), 
        index=list(unique_tokens),
        dtype=np.uint32,
    )
    
    for (pred, POS), descendants_list in connections.items():
        #print(f'{pred=}, {descendants=}')
        
        for descendants in descendants_list:
            #print(f'{descendants}')
            
            if POS != 'AUX':
                for (desc, weight) in descendants:
                    adj_mat.at[pred, desc] += weight
            
            else:
                if len(descendants) > 1:
                    # if auxiliary word, make connection between all associated words
                    combs = combinations(descendants, r=2)
                    
                    for comb in combs:
                        # comb is tuple ((word_1, weight), (word_2, weight))
                        weight = comb[0][1]
                        word_1 = comb[0][0]
                        word_2 = comb[1][0]
                        
                        """
                        if ((word_1 == 'Eigenverantwortlichkeit' or word_1 == 'neu') and
                            (word_2 == 'Eigenverantwortlichkeit' or word_2 == 'neu')):
                            print(f'Hello from {pred=} with {descendants=}')
                        """
                        
                        adj_mat.at[word_1, word_2] += weight
    
    return adj_mat


def make_undir_adj_matrix(adj_mat):
    
    adj_mat_undir = adj_mat.copy()
    arr = adj_mat_undir.to_numpy()
    arr_upper = np.triu(arr)
    arr_lower = np.tril(arr)
    arr_lower = np.rot90(np.fliplr(arr_lower))
    arr_new = arr_lower + arr_upper
    
    adj_mat_undir.loc[:] = arr_new
    
    return adj_mat_undir

In [251]:
spacy.displacy.render(doc)

#### Gesamter Datensatz

In [252]:
# analysiere erste 10 Einträge
descr = temp1[['descr', 'num_occur']]
#descr = descr.iloc[:7,:]

In [253]:
#descr.iat[0,0] = 'Das ist ein Test am 24.08.2023'

In [254]:
len(descr)

6753

In [255]:
descr

descr num_occur
161   Tägliche Wartungstätigkeiten nach Vorgabe des ...     92592
33                Wöchentliche Sichtkontrolle Reinigung      1654
130               Tägliche Überprüfung der Ölabscheider      1616
159               Wöchentliche Kontrolle der WC-Anlagen      1265
139        Halbjährliche Kontrolle des Stabbreithalters       687
...                                                 ...       ...
2665  Überprüfung der Y-Achse Schneidbrücke am LC 2 ...         1
2664  Luftschlauch muss ausgetauscht werden. Ist und...         1
2663                 Riemenscheibe tauschen auf 650 UPM         1
2660                    Durchführung: Sollwert: 20 0,1g         1
6752  Befestigung Deckel für Batteriefach defekt Hal...         1

[6753 rows x 2 columns]

In [256]:
#LOAD_CALC_FILES = True
#LOAD_CALC_FILES = False
#IS_TEST = True
IS_TEST = False

In [257]:
spell_check_whitelist = {
    '',
    'beschlag',
    'brandschutztechnische',
    'dichtung',
    'festhaltevorrichtung',
    'funktion',
    'halbjährliche',
    'kontrolle',
    'maschinenhersteller',
    'prüfung',
    'reinigung',
    'scharnier',
    'schließvorrichtung',
    'schmierung',
    'sichtkontrolle',
    'stabbreithalter',
    'technikrundgang',
    'vorgabe',
    'wartungstätigkeit',
    'wcanlage',
    'ölabscheider',
    'abarbeiten',
    'abgleichen',
    'abschmieren',
    'abschmierung',
    'abteilungsleiter',
    'akku',
    'analyse',
    'arbeitsplan',
    'aschenbecher',
    'auffüllen',
    'auflistung',
    'befestigungsschraube',
    'beschädigung',
    'betriebsstunde',
    'blombe',
    'blombieren',
    'brückner',
    'campenabwickler',
    'campenaufwickler',
    'desinfektionsmittel',
    'dichtigkeit',
    'druckkontrolle',
    'efficiosystem',
    'eigenverantwortlichkeit',
    'einrichtung',
    'email',
    'erledigungsdatum',
    'extradate',
    'extradatum',
    'filter',
    'firma',
    'formplatte',
    'frostprävention',
    'gegendruckbolze',
    'gesamtanlage',
    'heizungsanlage',
    'keller',
    'kesselhauskontrolle',
    'kesselwasser',
    'koffer',
    'kompensator',
    'kompressorstation',
    'kondensat',
    'kühlturm',
    'kühltürme',
    'lager',
    'laserabteilung',
    'leckage',
    'leerung',
    'leiterprüfung',
    'linearkugellager',
    'luftdruckkontrolle',
    'magazin',
    'maschinenbediener',
    'messwert',
    'monat',
    'motor',
    'papiermüllbehälter',
    'personalbüro',
    'pflasterschrank',
    'rieme',
    'rollenkette',
    'rundgang',
    'schweißkopf',
    'schweisskopf',
    'sichtprüfung',
    'speisewasser',
    'sprinkleranlage',
    'temperatursensor',
    'terminieren',
    'ticket',
    'trommel',
    'täglicher',
    'uvröhre',
    'ventilator',
    'verbandsmaterial',
    'verschleiß',
    'verschleiss',
    'vorbelegung',
    'wartung',
    'wartungsarbeit',
    'wartungsplan',
    'wasseraufbereitung',
    'wasseraufbereitungsanlage',
    'wasserverbrauch',
    'weberei',
    'wumagtrockner',
    'wäscherkontrolle',
    'wöchig',
    'abdichten',
    'abfluprüfung',
    'ablesen',
    'abluftkanal',
    'absauganlage',
    'abspeichern',
    'absprache',
    'aktivkohlepatron',
    'aktivkohlepatrone',
    'anbackung',
    'anfragen',
    'angebot',
    'anpresswalze',
    'ansaug',
    'anschluss',
    'anschluß',
    'anzahl',
    'auen',
    'auenbereich',
    'aueneinheit',
    'aufwickler',
    'ausblasöffnung',
    'ausbrennen',
    'auslassventil',
    'ausrüstung',
    'austausch',
    'axialpendelrollenlager',
    'batteriewechsel',
    'batterieüberprüfung',
    'baugruppe',
    'baumwolltuch',
    'bauteil',
    'befeuchter',
    'beleuchtung',
    'beschichtunglegierung',
    'besprechungszimmer',
    'bestandskontrolle',
    'bestellformular',
    'bestätigung',
    'bezeichnung',
    'binder',
    'blutstop',
    'bolze',
    'breitstreckwalze',
    'containerstellfläche',
    'contrawalze',
    'dachfläche',
    'dampfzylinder',
    'deformierung',
    'dezember',
    'din',
    'docke',
    'dokumentation',
    'dosierpumpe',
    'druckluftbehälter',
    'druckluftleitung',
    'druckluftschläuche',
    'drucktestkontrolle',
    'einterminieren',
    'eintragung',
    'einzelprotokoll',
    'einziehwalze',
    'elektisch',
    'element',
    'enthärtung',
    'entwässern',
    'erledigungsbeschreibeung',
    'erstehilfeeinrichtung',
    'erweiterung',
    'explosionsschutzanlage',
    'extradaten',
    'exzenterringbefestigung',
    'fa',
    'fach',
    'faltenbalge',
    'feedbackinput',
    'feuerwehrumfahrung',
    'filert',
    'filteranlage',
    'filterelement',
    'filterstufe',
    'fixtermin',
    'flanschlager',
    'flanschlagerquadrat',
    'fluchtwegsymbol',
    'flusenabsaugrohr',
    'freilauf',
    'fremdkörper',
    'führungswagen',
    'gaslager',
    'gaszählerstand',
    'gatter',
    'geräteinner',
    'geräteinneres',
    'geräusch',
    'gesamt',
    'gesamterzeugt',
    'getränkeautomat',
    'gewindebefestigung',
    'gewindestiftbefestigung',
    'gleitschiene',
    'grat',
    'gro',
    'grundplatte',
    'halle',
    'haupteingang',
    'hebebühne',
    'hebezeug',
    'helm',
    'hersteller',
    'hochregal',
    'hochtemperatur',
    'hochtemperatureinsatz',
    'hydraulik',
    'hydrauliköl',
    'impulseingang',
    'indikator',
    'inneneinheit',
    'insektenvernichter',
    'kabel',
    'kammer',
    'karton',
    'kegelradgetriebe',
    'kegelradgetriebemotor',
    'kette',
    'klemmrolle',
    'klimaanlage',
    'klimabühne',
    'klimagerät',
    'kompressor',
    'kompressorluftwert',
    'kontoll',
    'kontrawalze',
    'kontroll',
    'krankheit',
    'krän',
    'kräne',
    'kuehlaggregat',
    'kw',
    'kühlgerät',
    'lagereinheit',
    'lagereinsatz',
    'lagerort',
    'lagerung',
    'laser',
    'laufgeräusche',
    'luftansaugseite',
    'luftfilter',
    'luftfilterwasserabscheider',
    'luftmenge',
    'luftreiniger',
    'lösungsmittel',
    'lüftungsanlage',
    'macke',
    'managementsystem',
    'maschinenanschluss',
    'materialzersetzung',
    'messlager',
    'micron',
    'mischer',
    'monatlicher',
    'monatliches',
    'monteur',
    'moos',
    'motorstart',
    'nachfetten',
    'nachschmieren',
    'nachspann',
    'neuvertrag',
    'nord',
    'nottelefon',
    'nr',
    'oberer',
    'oberflächenkontrolle',
    'objektkarte',
    'palette',
    'pendelkugellager',
    'pfeifer',
    'platine',
    'pneum',
    'pneumatikventil',
    'pneumatisch',
    'pos',
    'positioniersystem',
    'prozesskennzahl',
    'prüfbericht',
    'prüfplan',
    'rampenbereich',
    'rauwalze',
    'regalprüfer',
    'regalsicherungsanlage',
    'reiniger',
    'reinigungstuch',
    'restlich',
    'risikoersatzteil',
    'rohrtrenner',
    'roller',
    'rundgangkontrollen',
    'rückmeldung',
    'sae',
    'sauberkeit',
    'schlitten',
    'schmierstoff',
    'schmierstoffmenge',
    'schneider',
    'schraube',
    'schraubenbestand',
    'schutzabdeckung',
    'sicherheitsbeleuchtung',
    'sicherheitseinrichtung',
    'sicherheitslichtschranke',
    'sicherheitsweste',
    'sicherstellung',
    'sonotrode',
    'sonotrodenständer',
    'spannkopflager',
    'spannlager',
    'spannrahmen',
    'spindel',
    'spindelhubgetriebe',
    'spindelmutter',
    'spülzeitprüfung',
    'stab',
    'stadtwasser',
    'stehlager',
    'stehlagergehäuse',
    'steuerung',
    'stückliste',
    'systemumstellung',
    'telefonanlage',
    'telefonat',
    'termin',
    'terminabsprache',
    'terminiern',
    'terminiert',
    'terminierung',
    'terminvorschlag',
    'testomat',
    'thermoheizelement',
    'torsprechanlage',
    'trinkwassernetz',
    'trockenzylinder',
    'tänzerrolle',
    'türdichtung',
    'türgriff',
    'türsicherung',
    'umlenkwalzen',
    'umrandung',
    'unkraut',
    'uschienenführung',
    'uvv',
    'ventil',
    'verbaut',
    'verbrennungsset',
    'vereinbarung',
    'verkalkung',
    'verschleiteileinsatz',
    'verschmutzung',
    'verschmutzungenlos',
    'verstellung',
    'verunreinigung',
    'vollständigkeit',
    'volumenzähler',
    'vorderer',
    'vordruck',
    'vorfilter',
    'vorfilterflie',
    'vorliegen',
    'vormonat',
    'wartungsintervall',
    'wartungsvertrag',
    'wasserfilter',
    'wasserhärte',
    'wasserpegelkontrolle',
    'wasserzählerstand',
    'wechselintervall',
    'wärmetauscher',
    'zahnrieme',
    'zahnstange',
    'zuleitung',
    'zuschicken',
    'ölfüllung',
    'ölstand',
    'ölstandsichtprüfung',
    'ölstandskontrolle',
    'überziehen'
}

In [258]:
corrections: dict[str, str] = {
    'desifektionsmittel': 'desinfektionsmittel',
    'schweikopf': 'schweisskopf',
}

**Entdeckte Gruppen**
- Prüfung:
    - Prüfen
    - Sichtprüfung
    - Überprüfung / überprüfen
    - Kontrolle / kontrollieren
    - sicherstellen / Sicherstellung
    - Wartung / warten
    - Reinigung / reinigen
    - Prüfbericht
- Handlung:
    - Schmierung
    - schmieren
    - reinigen
    - Reinigung
    - schneiden / nachschneiden
- zyklisch:
    - täglich
    - wöchentlich
    - monatlich
    - jährlich
- Datum:
    - Uhr
    - Montag, Dienstag, Mittwoch, Donnerstag, Freitag, Samstag, Sonntag
- Kleinteile:
    - Schraube
    - Adapter
    - Halterung
    - Scheibe
    - Gewinde
    - Ventil
    - Schalter
    - Befestigungsschraube
- Komponenten:
    - Kupplung
    - Motor
    - Getriebe
    - Ventilator
    - Zahnriemen
    - Tranformator
    - Filterelement
    - Dosierpumpe
    - Luftschlauch
    - Dichtung
    - Filter
    - Scharnier
    - Spannrolle
    - Druckluftbehälter
    - Kette
    - Anschlüsse
    - Schläuche
    - Beleuchtung
- Elektrik:
    - Zuleitung
    - Kabel
    - Steckdose
    - Elektriker
    - Elektronik
    - elektrisch
    - Sicherheitsbeleuchtung
- Anlagen:
    - Mischanlage
    - Maschine
    - Wasserenthärtungsanlage
    - Lüftungsanlage
    - Klimaanlage
- Vereinbarung:
    - Wartungsvertrag
    - Neuvertrag
    - Vertrag
    - terminieren / terminiert
    - Absprache
    - melden
    - telefonisch
    - mitteilen
- Störbild:
    - defekt
    - kaputt
    - Geräusch
    - undicht
    - leckt
    - Dichtigkeit
- Abteilung:
    - Buchhaltung
    - Betriebstechnik
    - Entwicklung
- Ort:
    - Kesselhaus
    - Durchfahrt
    - Dach
    - Haupteingang
    - Werkbank
    - Schlosserei

In [272]:
word_2_map = {
    'Prüfung': ['prüfen', 'sichtprüfung', 'überprüfung', 'überprüfen',
                'kontrolle', 'kontrollieren', 'sicherstellen', 'sicherstellung',
                'reinigung', 'reinigen', 'prüfbericht', 'sichtkontrolle',
                'rundgang', 'technikrundgang'],
    'Wartung': ['wartung', 'warten', 'wartungstätigkeit', 'wartungsarbeit',
                'wartungsplan'],
    'Handlung': ['schmierung', 'schmieren', 'reinigen', 'reinigung',
                 'schneiden', 'nachschneiden'],
    'zyklisch': ['täglich', 'tägliche', 'täglicher', 'wöchentlich', 'wöchentliche', 'monatlich', 'jährlich',
                 'halbjährlich', 'monatliche', 'wartungsintervall'],
    'Datum': ['uhr', 'montag', 'dienstag', 'mittwoch', 'donnerstag',
              'freitag', 'samstag', 'sonntag'],
    'Kleinteile': ['schraube', 'adapter', 'halterung', 'scheibe', 'gewinde',
                   'ventil', 'schalter', 'befestigungsschraube'],
    'Komponenten': ['kupplung', 'motor', 'getriebe', 'ventilator',
                    'zahnriemen', 'transformator', 'filterelement',
                    'dosierpumpe', 'luftschlauch', 'dichtung', 'filter',
                    'scharnier', 'spannrolle', 'druckluftbehälter', 'kette',
                    'anschlüsse', 'anschluss', 'schläuche', 'schlauch', 'beleuchtung'],
    'Elektrik': ['zuleitung', 'kabel', 'steckdose', 'elektriker',
                 'elektronik', 'elektrisch', 'sicherheitsbeleuchtung'],
    'Anlagen': ['anlage', 'mischanlage', 'maschine', 'klimaanlage', 'filteranlage',
                'wasserenthärtungsanlage', 'lüftungsanlage', 'wasseraufbereitungsanlage'],
    'Vereinbarung': ['wartungsvertrag', 'neuvertrag', 'vertrag', 'terminieren'
                     'terminiert', 'absprache', 'melden', 'telefonisch', 'mitteilen'],
    'Störbild': ['defekt', 'kaputt', 'geräusch', 'undicht', 'leckt', 'dichtigkeit'],
    'Abteilung': ['buchhaltung', 'betriebstechnik', 'entwicklung'],
    'Ort': ['kesselhaus', 'durchfahrt', 'dach', 
            'haupteingang', 'werkbank', 'schlosserei'],
}

- Frage: Existiert Möglichkeit zur Klassifizierung von Begriffen?
    - z.B. automatische Kennung, ob Komponente oder nicht

In [273]:
map_2_word = dict()

for key, word_list in word_2_map.items():
    
    for word in word_list:
        map_2_word[word] = key

In [274]:
# adjacency matrix
connections = dict()
unique_tokens = set()
UPDATE_STATUS = 500
length_data = len(descr)
spell_check_candidates = set()
spell_checker = SpellChecker(language='de', distance=1)

if not LOAD_CALC_FILES or IS_TEST:
    for count, description in enumerate(descr.iterrows()):
        
        text = description[1]['descr']
        weight = description[1]['num_occur']
        
        doc = nlp(text)
        
        obtain_descendant_info(
            doc=doc,
            weight=weight,
            POS_of_interest=POS_of_interest,
            TAG_of_interest=TAG_of_interest,
            connections=connections,
            unique_tokens=unique_tokens,
            spell_check_candidates=spell_check_candidates,
            spell_check_whitelist=spell_check_whitelist,
            spell_checker=spell_checker,
            corrections=corrections,
            map_2_word=map_2_word,
        )
        
        if count % UPDATE_STATUS == 0:
            logger.info(f'Number of entries processed: {count+1}, Percent completed: {((count+1) / length_data) * 100:.2f}')

INFO:base:Number of entries processed: 1, Percent completed: 0.01


INFO:base:Number of entries processed: 501, Percent completed: 7.42
INFO:base:Number of entries processed: 1001, Percent completed: 14.82
INFO:base:Number of entries processed: 1501, Percent completed: 22.23
INFO:base:Number of entries processed: 2001, Percent completed: 29.63
INFO:base:Number of entries processed: 2501, Percent completed: 37.04
INFO:base:Number of entries processed: 3001, Percent completed: 44.44
INFO:base:Number of entries processed: 3501, Percent completed: 51.84
INFO:base:Number of entries processed: 4001, Percent completed: 59.25
INFO:base:Number of entries processed: 4501, Percent completed: 66.65
INFO:base:Number of entries processed: 5001, Percent completed: 74.06
INFO:base:Number of entries processed: 5501, Percent completed: 81.46
INFO:base:Number of entries processed: 6001, Percent completed: 88.86
INFO:base:Number of entries processed: 6501, Percent completed: 96.27


In [275]:
ADJ_DF_PATH = './Graphanalyse/adj_mat_df.fth'
if not IS_TEST:
    if LOAD_CALC_FILES:
        adj_mat_undir = pd.read_feather(ADJ_DF_PATH)
        adj_mat_undir = adj_mat_undir.set_index('index')
        # additional information
        connections = load_pickle('connections.pkl')
        unique_tokens = load_pickle('unique_tokens.pkl')
    else:
        adj_mat = obtain_adj_matrix(unique_tokens=unique_tokens, connections=connections)
        adj_mat_undir = make_undir_adj_matrix(adj_mat=adj_mat)
        save_df = adj_mat_undir.reset_index()
        save_df.to_feather(ADJ_DF_PATH)
        # additional information
        save_pickle(obj=connections, path='connections.pkl')
        save_pickle(obj=unique_tokens, path='unique_tokens.pkl')

In [276]:
adj_mat_undir.sort_index()

Klübertemp  Schusssuche  Laser  Schaftteile  Dichtsätz  \
A                      0            0      0            0          0   
ACHTUNG                0            0      0            0          0   
ACServomotor           0            0      0            0          0   
AForm                  0            0      0            0          0   
AIB                    0            0      0            0          0   
...                  ...          ...    ...          ...        ...   
überziech              0            0      0            0          0   
überziehen             0            0      0            0          0   
überzogen              0            0      0            0          0   
üblich                 0            0      0            0          0   
üperprüfen             0            0      0            0          0   

              Tastatur  Vorspuleinheit  beginnen  auslesen  Kettspannung  ...  \
A                    0               0         0         0             0  ...   
ACHTUNG              0               0         0         0             0  ...   
ACServomotor         0               0         0         0             0  ...   
AForm                0               0         0         0             0  ...   
AIB                  0               0         0         0             0  ...   
...                ...             ...       ...       ...           ...  ...   
überziech            0               0         0         0             0  ...   
überziehen           0               0         0         0             0  ...   
überzogen            0               0         0         0             0  ...   
üblich               0               0         0         0             0  ...   
üperprüfen           0               0         0         0             0  ...   

              Tänzerwalze  Abfallkante  rappeln  Rottenegger  Contrawalze  \
A                       0            0        0            0            0   
ACHTUNG                 0            0        0            0            0   
ACServomotor            0            0        0            0            0   
AForm                   0            0        0            0            0   
AIB                     0            0        0            0            0   
...                   ...          ...      ...          ...          ...   
überziech               0            0        0            0            0   
überziehen              0            0        0            0           17   
überzogen               0            0        0            0            6   
üblich                  0            0        0            0            0   
üperprüfen              0            0        0            0            0   

              Eisenträger  Hängegurte  Treffen  Greiferarmen  Nadelleist  
A                       0           0        0             0           0  
ACHTUNG                 0           0        0             0           0  
ACServomotor            0           0        0             0           0  
AForm                   0           0        0             0           0  
AIB                     0           0        0             0           0  
...                   ...         ...      ...           ...         ...  
überziech               0           0        0             0           0  
überziehen              0           0        0             0           0  
überzogen               0           0        0             0           0  
üblich                  0           0        0             0           0  
üperprüfen              0           0        0             0           0  

[6845 rows x 6845 columns]

Test Cosine Similarity
- erstelle Matrix mit Ähnlichkeits-Score (obere Dreiecksmatrix)
- jedes Wortpaar
- filtere Tabelle nach Threshold
- nutze Gewichts-Adjezenzmatrix mit Threshold als Maske
    - nur Analyse von hochgewichtigen Gruppen
- analysiere Zusammenhänge in Form von Graph (ähnlich bisherigem Vorgehen)
- bilde Gruppen und benenne diese (z.B. Prüfung+Überprüfung+Kontrolle --> Überprüfung)
- baue daraus Wörterbuch und matche Begriffe bei der Erstellung

In [49]:
def build_cosine_similarity_matrix(
    adj_mat
):
    # obtain words to compare
    words = adj_mat.index.to_list()
    
    # cos matrix
    cos_mat = pd.DataFrame(
        data=0., 
        columns=words, 
        index=words,
        dtype=np.float32,
    )
    
    for (word1, word2) in combinations(words, 2):
        # obtain model vocabulary
        w1 = nlp.vocab[str(word1)]
        w2 = nlp.vocab[str(word2)]
        # calculate cosine similarity
        cos_sim = w1.similarity(w2)
        # set value
        cos_mat.at[word1, word2] = cos_sim
        
    return cos_mat

In [50]:
cos_mat = build_cosine_similarity_matrix(adj_mat=adj_mat_undir)

C:\Users\foersterflorian\AppData\Local\Temp\ipykernel_17216\213623562.py:20: UserWarning: [W008] Evaluating Lexeme.similarity based on empty vectors.
  cos_sim = w1.similarity(w2)


In [52]:
cos_mat

Klübertemp  Schusssuche  Laser  Schaftteile  Dichtsätz  \
Klübertemp           0.0          0.0    0.0          0.0        0.0   
Schusssuche          0.0          0.0    0.0          0.0        0.0   
Laser                0.0          0.0    0.0          0.0        0.0   
Schaftteile          0.0          0.0    0.0          0.0        0.0   
Dichtsätz            0.0          0.0    0.0          0.0        0.0   
...                  ...          ...    ...          ...        ...   
Eisenträger          0.0          0.0    0.0          0.0        0.0   
Hängegurte           0.0          0.0    0.0          0.0        0.0   
Treffen              0.0          0.0    0.0          0.0        0.0   
Greiferarmen         0.0          0.0    0.0          0.0        0.0   
Nadelleist           0.0          0.0    0.0          0.0        0.0   

              Tastatur  Vorspuleinheit  beginnen  auslesen  Kettspannung  ...  \
Klübertemp    0.000000             0.0  0.000000  0.000000           0.0  ...   
Schusssuche   0.000000             0.0  0.000000  0.000000           0.0  ...   
Laser         0.324276             0.0  0.059743  0.133676           0.0  ...   
Schaftteile   0.000000             0.0  0.000000  0.000000           0.0  ...   
Dichtsätz     0.000000             0.0  0.000000  0.000000           0.0  ...   
...                ...             ...       ...       ...           ...  ...   
Eisenträger   0.000000             0.0  0.000000  0.000000           0.0  ...   
Hängegurte    0.000000             0.0  0.000000  0.000000           0.0  ...   
Treffen       0.000000             0.0  0.000000  0.000000           0.0  ...   
Greiferarmen  0.000000             0.0  0.000000  0.000000           0.0  ...   
Nadelleist    0.000000             0.0  0.000000  0.000000           0.0  ...   

              Tänzerwalze  Abfallkante   rappeln  Rottenegger  Contrawalze  \
Klübertemp            0.0          0.0  0.000000          0.0          0.0   
Schusssuche           0.0          0.0  0.000000          0.0          0.0   
Laser                 0.0          0.0 -0.063913          0.0          0.0   
Schaftteile           0.0          0.0  0.000000          0.0          0.0   
Dichtsätz             0.0          0.0  0.000000          0.0          0.0   
...                   ...          ...       ...          ...          ...   
Eisenträger           0.0          0.0  0.000000          0.0          0.0   
Hängegurte            0.0          0.0  0.000000          0.0          0.0   
Treffen               0.0          0.0  0.000000          0.0          0.0   
Greiferarmen          0.0          0.0  0.000000          0.0          0.0   
Nadelleist            0.0          0.0  0.000000          0.0          0.0   

              Eisenträger  Hängegurte   Treffen  Greiferarmen  Nadelleist  
Klübertemp       0.000000         0.0  0.000000           0.0         0.0  
Schusssuche      0.000000         0.0  0.000000           0.0         0.0  
Laser            0.167521         0.0 -0.029860           0.0         0.0  
Schaftteile      0.000000         0.0  0.000000           0.0         0.0  
Dichtsätz        0.000000         0.0  0.000000           0.0         0.0  
...                   ...         ...       ...           ...         ...  
Eisenträger      0.000000         0.0  0.170954           0.0         0.0  
Hängegurte       0.000000         0.0  0.000000           0.0         0.0  
Treffen          0.000000         0.0  0.000000           0.0         0.0  
Greiferarmen     0.000000         0.0  0.000000           0.0         0.0  
Nadelleist       0.000000         0.0  0.000000           0.0         0.0  

[6951 rows x 6951 columns]

In [635]:
WEIGHT_THRESHOLD = 10
arr = adj_mat_undir.to_numpy()
COS_THRESHOLD = 0.4
cos_arr = cos_mat.to_numpy()

In [636]:
cos_arr_filt = np.where((cos_arr > COS_THRESHOLD) & (arr >= WEIGHT_THRESHOLD), cos_arr, 0)

In [637]:
cos_arr_filt

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)

In [638]:
np.count_nonzero(cos_arr_filt)

217

In [639]:
thresh_cos_mat = cos_mat.copy()
thresh_cos_mat[:] = cos_arr_filt

In [640]:
thresh_cos_mat

Verstärkung  Zuluftfilter  klemmt  Komminikation  \
Verstärkung               0.0           0.0     0.0            0.0   
Zuluftfilter              0.0           0.0     0.0            0.0   
klemmt                    0.0           0.0     0.0            0.0   
Komminikation             0.0           0.0     0.0            0.0   
Doppelholztische          0.0           0.0     0.0            0.0   
...                       ...           ...     ...            ...   
Mitarbeiterin             0.0           0.0     0.0            0.0   
Nägel                     0.0           0.0     0.0            0.0   
WZ                        0.0           0.0     0.0            0.0   
ExSchutzAnlage            0.0           0.0     0.0            0.0   
Gemisch                   0.0           0.0     0.0            0.0   

                  Doppelholztische  Deckenbeleuchtung  Abfalltransport  \
Verstärkung                    0.0                0.0              0.0   
Zuluftfilter                   0.0                0.0              0.0   
klemmt                         0.0                0.0              0.0   
Komminikation                  0.0                0.0              0.0   
Doppelholztische               0.0                0.0              0.0   
...                            ...                ...              ...   
Mitarbeiterin                  0.0                0.0              0.0   
Nägel                          0.0                0.0              0.0   
WZ                             0.0                0.0              0.0   
ExSchutzAnlage                 0.0                0.0              0.0   
Gemisch                        0.0                0.0              0.0   

                  fahrbar  Folieneinlauf  entsorgen  ...  neuwertig  Bleit  \
Verstärkung           0.0            0.0        0.0  ...        0.0    0.0   
Zuluftfilter          0.0            0.0        0.0  ...        0.0    0.0   
klemmt                0.0            0.0        0.0  ...        0.0    0.0   
Komminikation         0.0            0.0        0.0  ...        0.0    0.0   
Doppelholztische      0.0            0.0        0.0  ...        0.0    0.0   
...                   ...            ...        ...  ...        ...    ...   
Mitarbeiterin         0.0            0.0        0.0  ...        0.0    0.0   
Nägel                 0.0            0.0        0.0  ...        0.0    0.0   
WZ                    0.0            0.0        0.0  ...        0.0    0.0   
ExSchutzAnlage        0.0            0.0        0.0  ...        0.0    0.0   
Gemisch               0.0            0.0        0.0  ...        0.0    0.0   

                  Rauchentwicklung  Kompressorsteuerung  anziehen  \
Verstärkung                    0.0                  0.0       0.0   
Zuluftfilter                   0.0                  0.0       0.0   
klemmt                         0.0                  0.0       0.0   
Komminikation                  0.0                  0.0       0.0   
Doppelholztische               0.0                  0.0       0.0   
...                            ...                  ...       ...   
Mitarbeiterin                  0.0                  0.0       0.0   
Nägel                          0.0                  0.0       0.0   
WZ                             0.0                  0.0       0.0   
ExSchutzAnlage                 0.0                  0.0       0.0   
Gemisch                        0.0                  0.0       0.0   

                  Mitarbeiterin  Nägel   WZ  ExSchutzAnlage  Gemisch  
Verstärkung                 0.0    0.0  0.0             0.0      0.0  
Zuluftfilter                0.0    0.0  0.0             0.0      0.0  
klemmt                      0.0    0.0  0.0             0.0      0.0  
Komminikation               0.0    0.0  0.0             0.0      0.0  
Doppelholztische            0.0    0.0  0.0             0.0      0.0  
...                         ...    ...  ...             ...      ...  
Mitarbeiterin            

In [641]:
COS_MAT_PATH_CSV = f'./Graphanalyse_Gruppen/cos_mat_Wthresh_{WEIGHT_THRESHOLD}_Cthresh{int(COS_THRESHOLD*100)}.csv'
thresh_cos_mat.to_csv(path_or_buf=COS_MAT_PATH_CSV, encoding='cp1252', sep=';')

In [603]:
arr = adj_mat_undir.to_numpy()

In [604]:
np.count_nonzero(arr)

24725

In [605]:
np.max(arr)

92788

In [606]:
uni_arr = np.unique(arr)
len(uni_arr)

257

Threshold

In [277]:
WEIGHT_THRESHOLD = 50
arr = adj_mat_undir.to_numpy()
arr = np.where(arr < WEIGHT_THRESHOLD, 0, arr)

In [278]:
np.count_nonzero(arr)

600

In [279]:
temp = np.sum(arr, axis=0)
np.count_nonzero(temp)

216

In [280]:
thresh_adj_mat = adj_mat_undir.copy()
thresh_adj_mat.loc[:] = arr

In [281]:
thresh_adj_mat

Klübertemp  Schusssuche  Laser  Schaftteile  Dichtsätz  \
Klübertemp             0            0      0            0          0   
Schusssuche            0            0      0            0          0   
Laser                  0            0      0            0          0   
Schaftteile            0            0      0            0          0   
Dichtsätz              0            0      0            0          0   
...                  ...          ...    ...          ...        ...   
Eisenträger            0            0      0            0          0   
Hängegurte             0            0      0            0          0   
Treffen                0            0      0            0          0   
Greiferarmen           0            0      0            0          0   
Nadelleist             0            0      0            0          0   

              Tastatur  Vorspuleinheit  beginnen  auslesen  Kettspannung  ...  \
Klübertemp           0               0         0         0             0  ...   
Schusssuche          0               0         0         0             0  ...   
Laser                0               0         0         0             0  ...   
Schaftteile          0               0         0         0             0  ...   
Dichtsätz            0               0         0         0             0  ...   
...                ...             ...       ...       ...           ...  ...   
Eisenträger          0               0         0         0             0  ...   
Hängegurte           0               0         0         0             0  ...   
Treffen              0               0         0         0             0  ...   
Greiferarmen         0               0         0         0             0  ...   
Nadelleist           0               0         0         0             0  ...   

              Tänzerwalze  Abfallkante  rappeln  Rottenegger  Contrawalze  \
Klübertemp              0            0        0            0            0   
Schusssuche             0            0        0            0            0   
Laser                   0            0        0            0            0   
Schaftteile             0            0        0            0            0   
Dichtsätz               0            0        0            0            0   
...                   ...          ...      ...          ...          ...   
Eisenträger             0            0        0            0            0   
Hängegurte              0            0        0            0            0   
Treffen                 0            0        0            0            0   
Greiferarmen            0            0        0            0            0   
Nadelleist              0            0        0            0            0   

              Eisenträger  Hängegurte  Treffen  Greiferarmen  Nadelleist  
Klübertemp              0           0        0             0           0  
Schusssuche             0           0        0             0           0  
Laser                   0           0        0             0           0  
Schaftteile             0           0        0             0           0  
Dichtsätz               0           0        0             0           0  
...                   ...         ...      ...           ...         ...  
Eisenträger             0           0        0             0           0  
Hängegurte              0           0        0             0           0  
Treffen                 0           0        0             0           0  
Greiferarmen            0           0        0             0           0  
Nadelleist              0           0        0             0           0  

[6845 rows x 6845 columns]

In [282]:
ADJ_MAT_PATH_CSV = f'./Graphanalyse_Gruppen/adj_mat_thresh_mapping_{WEIGHT_THRESHOLD}.csv'
thresh_adj_mat.to_csv(path_or_buf=ADJ_MAT_PATH_CSV, encoding='cp1252', sep=';')

***Testing***

In [208]:
important_words = []
all_entities = []
pos_tags = set()
pos_counter = dict()
token_counter = 0

for description in descr:
    doc = nlp(description)
    
    relevant_words = []
    for token in doc:
        POS = token.pos_
        token_counter += 1
        if POS in pos_counter:
            pos_counter[POS] += 1
        else:
            pos_counter[POS] = 1
        
        if (not token.is_stop and not token.is_punct and 
            not token.is_space and (POS == 'NOUN' or 
                                    POS == 'PROPN' or 
                                    POS == 'ADJ' or 
                                    POS == 'ADV')):
            relevant_words.append((token.lemma_.lower(), POS))
            #pos_tags.add(token.pos_)
    
    entities = [] 
    for ent in doc.ents:
        entities.append((ent.text, ent.label_))
    
    important_words.extend(relevant_words)
    all_entities.extend(entities)

In [209]:
important_words

[('descr', 'ADV'), ('num_occur', 'NOUN')]

In [210]:
len(important_words)

2

In [211]:
all_entities

[('descr', 'LOC'), ('num_occur', 'MISC')]

In [ ]:
count = Counter(important_words)

In [ ]:
count

Counter({('täglich', 'ADJ'): 3,
         ('prüfung', 'NOUN'): 3,
         ('sichtkontrolle', 'NOUN'): 2,
         ('kontrolle', 'NOUN'): 2,
         ('scharniere', 'NOUN'): 2,
         ('dichtung', 'NOUN'): 2,
         ('schließvorrichtung', 'NOUN'): 2,
         ('schloß', 'NOUN'): 2,
         ('beschlag', 'NOUN'): 2,
         ('allgemein', 'ADJ'): 2,
         ('funktion', 'NOUN'): 2,
         ('schmierung', 'NOUN'): 2,
         ('festhaltevorrichtung', 'NOUN'): 2,
         ('monatliche', 'ADJ'): 2,
         ('wartungstätigkeit', 'NOUN'): 1,
         ('vorgabe', 'NOUN'): 1,
         ('maschinenhersteller', 'NOUN'): 1,
         ('wöchentliche', 'ADJ'): 1,
         ('reinigung', 'NOUN'): 1,
         ('überprüfung', 'NOUN'): 1,
         ('ölabscheider', 'NOUN'): 1,
         ('wöchentlich', 'ADJ'): 1,
         ('wc-anlage', 'NOUN'): 1,
         ('halbjährliche', 'ADJ'): 1,
         ('stabbreithalter', 'NOUN'): 1,
         ('brandschutztechnische', 'ADJ'): 1,
         ('technikrundgang', 'N

In [ ]:
pos_count = pd.Series(data=pos_counter)
pos_count.sort_values(ascending=False)

NOUN     25722
PUNCT    11626
VERB      9093
ADP       7211
ADV       6526
PROPN     4481
NUM       4115
DET       3845
ADJ       2576
AUX       2329
PART      1561
CCONJ     1305
X          999
PRON       916
SCONJ      385
SPACE      236
INTJ         1
dtype: int64

In [ ]:
pos_count_rel = pos_count / pos_count.sum()
pos_count_rel.sort_values(ascending=False)

NOUN     0.310176
PUNCT    0.140196
VERB     0.109651
ADP      0.086956
ADV      0.078696
PROPN    0.054035
NUM      0.049622
DET      0.046366
ADJ      0.031063
AUX      0.028085
PART     0.018824
CCONJ    0.015737
X        0.012047
PRON     0.011046
SCONJ    0.004643
SPACE    0.002846
INTJ     0.000012
dtype: float64

In [ ]:
token_counter

82927

### Weiterführende Analyse der Beschreibungen

- unklare Zusammenhänge der 1200er-Threshold-Ergebnisse präzisieren:
    - Finden der entsprechenden Beschreibungen
    - Kontextualisieren
- Identifikation von weiteren Blacklistworten

#### Unklare Zusammenhänge 1200er-Threshold

In [ ]:
temp1

descr  len  num_occur  \
index                                                                      
161    Tägliche Wartungstätigkeiten nach Vorgabe des ...   66      92592   
33                 Wöchentliche Sichtkontrolle Reinigung   37       1654   
130                Tägliche Überprüfung der Ölabscheider   37       1616   
159                Wöchentliche Kontrolle der WC-Anlagen   37       1265   
139         Halbjährliche Kontrolle des Stabbreithalters   44        687   
...                                                  ...  ...        ...   
2675   Stand 15.07.2020 Stöppel: Herr Langner Toyota ...  253          1   
2674   Zahnräder der Laufkatze verschlissen Ersatztei...  167          1   
2673     Bitte 8 Scheiben nach Muster anfertigen. Danke.   47          1   
2672   Schalter für Bühne Schwenken abgerissen, bitte...  123          1   
6781   Befestigung Deckel für Batteriefach defekt Hal...   99          1   

                                           assoc_obj_ids  num_assoc_obj_ids  
index                                                                        
161    [0, 17, 41, 42, 43, 44, 45, 46, 47, 51, 52, 53...                206  
33     [301, 304, 305, 313, 314, 331, 332, 510, 511, ...                 18  
130                                 [0, 970, 2134, 2137]                  4  
159    [1352, 1353, 1354, 1684, 1685, 1686, 1687, 168...                 11  
139    [51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 6...                166  
...                                                  ...                ...  
2675                                               [311]                  1  
2674                                               [415]                  1  
2673                                               [140]                  1  
2672                                               [323]                  1  
6781                                               [326]                  1  

[6782 rows x 5 columns]

In [ ]:
temp2 = temp1.loc[temp1['num_occur'] >= 3, :]
temp2 = temp1.copy()

In [ ]:
#temp2 = temp2.iloc[:30,:]

In [ ]:
check_words = set(['E1.8'])
target_indices = list()

for idx, row in temp2.iterrows():
    
    text = row['descr']
    doc = nlp(text)
    
    token_set = set()
    target_idx = None
    for token in doc:
            
        if not (token.pos_ in POS_of_interest or token.tag_ in TAG_of_interest):
            continue
        
        token_set.add(token.lemma_.lower())
        #print(f'{token_set=}')

    if token_set.issuperset(check_words):
        target_indices.append(idx)

In [ ]:
target_indices

[]

In [ ]:
idx = target_indices[3]
temp2.at[idx, 'descr']

'Vorgaben aus Pleva Wartungsplan Schmieren der Rollenlager der beiden Kameralaufschlitten des Strukturdetektors SD 1C siehe Extradaten'

In [ ]:
temp2.at[1921,'descr']

'Leiterprüfung derzeit in Arbeit Abteilungsleiter sind per Email am 11.06.2019 über deren Eigenverantwortlichkeit und Mithilfe durch Herr Graf informiert worden.'

In [ ]:
token_set.issuperset(check_words)

True

In [ ]:
POS_of_interest
TAG_of_interest

{'ADJD'}

In [ ]:
test = 'Tägliche, tägliche Wartungstätigkeit des Maschinenherstellers Maschine'

In [ ]:
doc = nlp(test)

In [ ]:
for token in doc:
    print(token.lemma_.lower())

täglich
--
täglich
wartungstätigkeit
der
maschinenhersteller
maschine


In [ ]:
replace_chars = [',', '\n', '\t', '\s']

In [ ]:
test = test.lower()
for char in replace_chars:
    test = test.replace(char, '')
test = test.split()
test = set(test)

In [ ]:
test

{'des', 'maschine', 'maschinenherstellers', 'tägliche', 'wartungstätigkeit'}

In [ ]:
test.issuperset(check_words)

False

**Zwischenergebnisse:**

*bestimmte ObjektIDs haben den Escape-Charakter, andere nicht: keine ObjektID mit beiden Varianten*

In [ ]:
print(f"Anzahl der Duplikate = {max_val} für Beschreibung mit Index-Nr. {index}:\n {text}")

Anzahl der Duplikate = 47689 für Beschreibung mit Index-Nr. 171:
 Tägliche Wartungstätigkeiten nach Vorgabe des Maschinenherstellers



---

# Merkmal 2: VorgangsArtText

In [53]:
feature = 'VorgangsArtText'

In [54]:
base = wo_duplicates.copy()
base = base.dropna(axis=0, subset=feature)
base[feature] = base[feature].map(clean_string)

In [55]:
base.head()

VorgangsID  ObjektID                                  HObjektText  \
0          11       114  427 C , Webmaschine, DL 280 EMS Breite 280    
1          17       124  621 C , Webmaschine, DL 280 EMS Breite 280    
2          53       244               285 C, Webmaschine, SG 220 EMS   
3          58       257                 107, Webmaschine, OM 220 EOS   
4          81       138                     00138, Schärmaschine 9,    

   ObjektArtID        ObjektArtText  VorgangsTypID            VorgangsTypName  \
0            3     Luft-Webmaschine              3  Reparaturauftrag (Portal)   
1            3     Luft-Webmaschine              3  Reparaturauftrag (Portal)   
2            5  Greifer-Webmaschine              3  Reparaturauftrag (Portal)   
3            3     Luft-Webmaschine              3  Reparaturauftrag (Portal)   
4           16        Schärmaschine              3  Reparaturauftrag (Portal)   

  VorgangsDatum  VorgangsStatusId  VorgangsPrioritaet  \
0    2019-03-06                 4                   0   
1    2019-03-11                 5                   0   
2    2019-03-19                 5                   0   
3    2019-03-21                 5                   0   
4    2019-03-25                 5                   0   

                       VorgangsBeschreibung VorgangsOrt  \
0                                       NaN         NaN   
1                                       NaN         NaN   
2                         Kupplung schleift         NaN   
3             Gegengewicht wieder anbringen         NaN   
4  da ist etwas gebrochen. (Herr Heininger)         NaN   

                                     VorgangsArtText ErledigungsDatum  \
0                                    Kettbaum kaputt       2019-03-06   
1                                            asgasdg       2019-03-11   
2                                    Kupplung defekt       2019-03-20   
3         Gegengewicht an der Webmaschine abgefallen       2019-03-21   
4  zentrale Bremsenverstellung linke Gatterseite ...       2019-03-25   

  ErledigungsArtText                            ErledigungsBeschreibung  \
0                NaN                                                NaN   
1                NaN                                                NaN   
2      Reparatur UTT                                                NaN   
3      Reparatur UTT  Schraube ausgebohrt\nGegengewicht wieder angeb...   
4      Reparatur UTT  Bolzen gebrochen. Bolzen neu angefertig und di...   

  MPMelderArbeitsplatz MPAbteilungBezeichnung Arbeitsbeginn ErstellungsDatum  
0              Weberei                Weberei           NaT       2019-03-06  
1     Elektrowerkstatt       Elektrowerkstatt           NaT       2019-03-11  
2              Weberei                Weberei           NaT       2019-03-19  
3              Weberei                Weberei    2019-03-21       2019-03-21  
4              Vorwerk                Vorwerk    2019-03-25       2019-03-25

In [56]:
descriptions = base[feature]
print(f"Einträge: {len(descriptions)}")

Einträge: 128936


In [57]:
num_dupl_descr = descriptions.duplicated().sum()
uni_descr = descriptions.unique()
num_uni_descr = len(uni_descr)

print(f"Anzahl Duplikate {feature}: {num_dupl_descr}")
print(f"Anzahl einzigartiger {feature}: {num_uni_descr}")
print(f"Anteil einzigartiger {feature}: {num_uni_descr / len(descriptions) * 100:.2f} %")

Anzahl Duplikate VorgangsArtText: 128545
Anzahl einzigartiger VorgangsArtText: 391
Anteil einzigartiger VorgangsArtText: 0.30 %


In [58]:
if not LOAD_CALC_FILES:
    cols = ['descr', 'len', 'num_occur', 'assoc_obj_ids', 'num_assoc_obj_ids']
    descr_df = pd.DataFrame(columns=cols)
    max_val = 0
    text = None
    index = 0


    for idx, description in enumerate(uni_descr):
        len_descr = len(description)
        filt = base[feature] == description
        temp = base[filt]
        assoc_obj_ids = temp['ObjektID'].unique()
        assoc_obj_ids = np.sort(assoc_obj_ids, kind='stable')
        num_assoc_obj_ids = len(assoc_obj_ids)
        num_dupl = filt.sum()
        
        conc_df = pd.DataFrame(data=[[
                                description,
                                len_descr,
                                num_dupl,
                                assoc_obj_ids,
                                num_assoc_obj_ids
                            ]], columns=cols)
        
        descr_df = pd.concat([descr_df, conc_df], ignore_index=True)
        
        if num_dupl > max_val:
            max_val = num_dupl
            index = idx
            text = description
            
    temp1 = descr_df.sort_values(by='num_occur', ascending=False)

In [59]:
temp1

descr len num_occur  \
60        Tägliche Interne Wartungstätigkeiten Weberei  44     92719   
10             01 Interne Reinigung Pflege Überprüfung  39     11250   
28             02 Interne Reinigung Pflege Überprüfung  39      3263   
29                       Maschinen-Wartung wöchentlich  29      2408   
46                Gesetzliche Wartung Prüfung jährlich  36      2403   
..                                                 ...  ..       ...   
222                     Walze WK 03 Umlenkwalze zapfen  30         1   
224                       Leiter Nr. 90 und überprüfen  28         1   
225                                   Locht nicht mehr  16         1   
226                    Maschine stellt immer wieder ab  31         1   
390  Gesetzliche Wartung Prüfung Anlagenprüfung Dru...  56         1   

                                         assoc_obj_ids num_assoc_obj_ids  
60   [0, 17, 41, 42, 43, 44, 45, 46, 47, 51, 52, 53...               206  
10   [0, 7, 425, 426, 427, 428, 429, 517, 518, 576,...               349  
28   [576, 906, 910, 940, 941, 942, 943, 1040, 1041...                52  
29   [1, 301, 305, 313, 314, 331, 332, 510, 511, 51...                25  
46   [0, 191, 193, 195, 197, 200, 287, 288, 289, 29...               638  
..                                                 ...               ...  
222                                                [1]                 1  
224                                                [1]                 1  
225                                              [338]                 1  
226                                              [338]                 1  
390                                              [547]                 1  

[391 rows x 5 columns]

In [60]:
# save/load dataframe
FILE_PATH = f'{feature}_analyse_1.fth'
if LOAD_CALC_FILES:
    temp1 = pd.read_feather(FILE_PATH)
    temp1 = temp1.set_index('index')
else:
    save_df = temp1.reset_index()
    save_df.to_feather(FILE_PATH)

#### Gesamter Datensatz

In [61]:
# analysiere erste 10 Einträge
descr = temp1[['descr', 'num_occur']]
#descr = descr.iloc[50:200,:]

In [62]:
#descr.iat[0,0] = 'Das ist ein Test am 24.08.2023'

In [63]:
len(descr)

391

In [64]:
descr

descr num_occur
60        Tägliche Interne Wartungstätigkeiten Weberei     92719
10             01 Interne Reinigung Pflege Überprüfung     11250
28             02 Interne Reinigung Pflege Überprüfung      3263
29                       Maschinen-Wartung wöchentlich      2408
46                Gesetzliche Wartung Prüfung jährlich      2403
..                                                 ...       ...
222                     Walze WK 03 Umlenkwalze zapfen         1
224                       Leiter Nr. 90 und überprüfen         1
225                                   Locht nicht mehr         1
226                    Maschine stellt immer wieder ab         1
390  Gesetzliche Wartung Prüfung Anlagenprüfung Dru...         1

[391 rows x 2 columns]

In [65]:
#LOAD_CALC_FILES = True
#LOAD_CALC_FILES = False
#IS_TEST = True
IS_TEST = False

In [66]:
# adjacency matrix
connections = dict()
unique_tokens = set()
UPDATE_STATUS = 100
length_data = len(descr)
spell_check_candidates = set()
spell_checker = SpellChecker(language='de', distance=1)

if not LOAD_CALC_FILES or IS_TEST:
    for count, description in enumerate(descr.iterrows()):
        
        text = description[1]['descr']
        weight = description[1]['num_occur']
        
        doc = nlp(text)
        
        obtain_descendant_info(
            doc=doc,
            weight=weight,
            POS_of_interest=POS_of_interest,
            TAG_of_interest=TAG_of_interest,
            connections=connections,
            unique_tokens=unique_tokens,
            spell_check_candidates=spell_check_candidates,
            spell_check_whitelist=spell_check_whitelist,
            spell_checker=spell_checker,
            corrections=corrections,
        )
        
        if count % UPDATE_STATUS == 0:
            logger.info(f'Number of entries processed: {count+1}, Percent completed: {((count+1) / length_data) * 100:.2f}')

INFO:base:Number of entries processed: 1, Percent completed: 0.26


INFO:base:Number of entries processed: 101, Percent completed: 25.83
INFO:base:Number of entries processed: 201, Percent completed: 51.41
INFO:base:Number of entries processed: 301, Percent completed: 76.98


In [67]:
ADJ_DF_PATH = f'./Graphanalyse/adj_mat_df_{feature}.fth'
if not IS_TEST:
    if LOAD_CALC_FILES:
        adj_mat_undir = pd.read_feather(ADJ_DF_PATH)
        adj_mat_undir = adj_mat_undir.set_index('index')
        # additional information
        connections = load_pickle('connections.pkl')
        unique_tokens = load_pickle('unique_tokens.pkl')
    else:
        adj_mat = obtain_adj_matrix(unique_tokens=unique_tokens, connections=connections)
        adj_mat_undir = make_undir_adj_matrix(adj_mat=adj_mat)
        save_df = adj_mat_undir.reset_index()
        save_df.to_feather(ADJ_DF_PATH)
        # additional information
        save_pickle(obj=connections, path='connections.pkl')
        save_pickle(obj=unique_tokens, path='unique_tokens.pkl')

In [68]:
adj_mat_undir.sort_index()

lecken  WC  LKW  offen  Maschinen-Reinigung  \
12-monatige-Inspektion       0   0    0      0                    0   
2-monatlich                  0   0    0      0                    0   
2-wöchentlich                0   0    0      0                    0   
24-monatige-Inspektion       0   0    0      0                    0   
3-jährlich                   0   0    0      0                    0   
...                        ...  ..  ...    ...                  ...   
Ölwechsel                    0   0    0      0                    0   
Überprüfung                  0   0    0      0                    0   
äußerer                      0   0    0      0                    0   
überprüfen                   0   0    0      0                    0   
überziehen                   0   0    0      0                    0   

                        Dockenwickler  halb-jährlich  Tisch  zentral  \
12-monatige-Inspektion              0              0      0        0   
2-monatlich                         0              0      0        0   
2-wöchentlich                       0              0      0        0   
24-monatige-Inspektion              0              0      0        0   
3-jährlich                          0              0      0        0   
...                               ...            ...    ...      ...   
Ölwechsel                           0              0      0        0   
Überprüfung                         0              0      0        0   
äußerer                             0              0      0        0   
überprüfen                          0              0      0        0   
überziehen                          0              0      0        0   

                        anbringen  ...  undicht-  Platine  erneuern  \
12-monatige-Inspektion          0  ...         0        0         0   
2-monatlich                     0  ...         0        0         0   
2-wöchentlich                   0  ...         0        0         0   
24-monatige-Inspektion          0  ...         0        0         0   
3-jährlich                      0  ...         0        0         0   
...                           ...  ...       ...      ...       ...   
Ölwechsel                       0  ...         0        0         0   
Überprüfung                     0  ...         0        0         0   
äußerer                         0  ...         0        0         0   
überprüfen                      0  ...         0        0         0   
überziehen                      0  ...         0        0         0   

                        Verschmutzung  befestigen  wechseln  Labor  Walze  \
12-monatige-Inspektion              0           0         0      0      0   
2-monatlich                         0           0         0      0      0   
2-wöchentlich                       0           0         0      0      0   
24-monatige-Inspektion              0           0         0      0      0   
3-jährlich                          0           0         0      0      0   
...                               ...         ...       ...    ...    ...   
Ölwechsel                           0           0         0      0      0   
Überprüfung                         0           0         0      0      0   
äußerer                             0           0         0      0      0   
überprüfen                          0           0         0      0      0   
überziehen                          0           0         0      0      1   

                        anfahren  Leiter  
12-monatige-Inspektion         0       0  
2-monatlich                    0       0  
2-wöchentlich                  0       0  
24-monatige-Inspektion         0       0  
3-jährlich                     0       0  
...                          ...     ...  
Ölwechsel                      0       0  
Überprüfung                    0       0  
äußerer                        0       0  
überprüfen                     0       1  
überziehen                     0       0  

[390 rows x

In [69]:
arr = adj_mat_undir.to_numpy()

In [70]:
np.count_nonzero(arr)

391

In [71]:
np.max(arr)

92964

Threshold

In [162]:
WEIGHT_THRESHOLD = 0

In [163]:
arr = adj_mat_undir.to_numpy()

In [164]:
arr = np.where(arr < WEIGHT_THRESHOLD, 0, arr)

In [165]:
np.count_nonzero(arr)

391

In [166]:
temp = np.sum(arr, axis=0)
np.count_nonzero(temp)

233

In [167]:
thresh_adj_mat = adj_mat_undir.copy()
thresh_adj_mat.loc[:] = arr

In [168]:
thresh_adj_mat

Wasserleitung  wechseln  Winkelpositionsgeber  \
Wasserleitung                        0         0                     0   
wechseln                             0         0                     0   
Winkelpositionsgeber                 0         0                     0   
Klimaanlagengerät                    0         0                     0   
versetzen                            0         0                     0   
...                                ...       ...                   ...   
haben                                0         0                     0   
Wasserenthärtungsanlage              0         0                     0   
Gestank                              0         0                     0   
Zahnrad                              0         0                     0   
hydraulisch                          0         0                     0   

                         Klimaanlagengerät  versetzen  Brennschlitten  \
Wasserleitung                            0          0               0   
wechseln                                 0          0               0   
Winkelpositionsgeber                     0          0               0   
Klimaanlagengerät                        0          0               0   
versetzen                                0          0               0   
...                                    ...        ...             ...   
haben                                    0          0               0   
Wasserenthärtungsanlage                  0          0               0   
Gestank                                  0          0               0   
Zahnrad                                  0          0               0   
hydraulisch                              0          0               0   

                         feststellen  Stuhl  monatlich  anfertigen  ...  \
Wasserleitung                      0      0          0           0  ...   
wechseln                           0      0          0           0  ...   
Winkelpositionsgeber               0      0          0           0  ...   
Klimaanlagengerät                  0      0          0           0  ...   
versetzen                          0      0          0           0  ...   
...                              ...    ...        ...         ...  ...   
haben                              0      0          0           0  ...   
Wasserenthärtungsanlage            0      0          0           0  ...   
Gestank                            0      0          0           0  ...   
Zahnrad                            0      0          0           0  ...   
hydraulisch                        0      0          0           0  ...   

                         Zahnriemen  Rampe  Tisch  defekt  Elektrische  haben  \
Wasserleitung                     0      0      0       0            0      0   
wechseln                          0      0      0       0            0      0   
Winkelpositionsgeber              0      0      0       1            0      0   
Klimaanlagengerät                 0      0      0       0            0      0   
versetzen                         0      0      0       0            0      0   
...                             ...    ...    ...     ...          ...    ...   
haben                             0      0      0       0            0      0   
Wasserenthärtungsanlage           0      0      0       0            0      0   
Gestank                           0      0      0       0            0      0   
Zahnrad                           0      0      0       0            0      0   
hydraulisch                       0      0      0       0            0      0   

                         Wasserenthärtungsanlage  Gestank  Zahnrad  \
Wasserleitung                                  0        0        0   
wechseln                                       0        0        0   
Winkelpositionsgeber                           0        0        0   
Klimaanlagengerät                              0        0        0   
versetzen                          

In [169]:
ADJ_MAT_PATH_CSV = f'./Graphanalyse/adj_mat_thresh_{feature}_{WEIGHT_THRESHOLD}.csv'
thresh_adj_mat.to_csv(path_or_buf=ADJ_MAT_PATH_CSV, encoding='cp1252', sep=';')

---

# Merkmal 3: ErledigungsBeschreibung

In [72]:
feature = 'ErledigungsBeschreibung'

In [73]:
base = wo_duplicates.copy()
base = base.dropna(axis=0, subset=feature)
base[feature] = base[feature].map(clean_string)

In [74]:
base.head()

VorgangsID  ObjektID                     HObjektText  ObjektArtID  \
3          58       257    107, Webmaschine, OM 220 EOS            3   
4          81       138        00138, Schärmaschine 9,            16   
5          82         0            Warenschau allgemein            0   
6          76         0                  Neben der Türe            0   
8         111       241  294 C, Webmaschine, SG 240 EMS            5   

         ObjektArtText  VorgangsTypID            VorgangsTypName  \
3     Luft-Webmaschine              3  Reparaturauftrag (Portal)   
4        Schärmaschine              3  Reparaturauftrag (Portal)   
5                  NaN              3  Reparaturauftrag (Portal)   
6                  NaN              3  Reparaturauftrag (Portal)   
8  Greifer-Webmaschine              3  Reparaturauftrag (Portal)   

  VorgangsDatum  VorgangsStatusId  VorgangsPrioritaet  \
3    2019-03-21                 5                   0   
4    2019-03-25                 5                   0   
5    2019-03-25                 5                   0   
6    2019-03-22                 5                   0   
8    2019-04-01                 5                   0   

                          VorgangsBeschreibung           VorgangsOrt  \
3                Gegengewicht wieder anbringen                   NaN   
4     da ist etwas gebrochen. (Herr Heininger)                   NaN   
5             Klappbügel Portalkran H31 defekt  Warenschau allgemein   
6                         Schraube nix mer gut        Neben der Türe   
8  KBK tauschen\nUrsache vermutlich mechanisch                   NaN   

                                     VorgangsArtText ErledigungsDatum  \
3         Gegengewicht an der Webmaschine abgefallen       2019-03-21   
4  zentrale Bremsenverstellung linke Gatterseite ...       2019-03-25   
5                      Allgemeine Reparaturarbeiten        2019-03-25   
6                                           Kettbaum       2019-03-25   
8                         Kupplung-Brems-Kombination       2019-04-08   

  ErledigungsArtText                            ErledigungsBeschreibung  \
3      Reparatur UTT  Schraube ausgebohrt Gegengewicht wieder angebr...   
4      Reparatur UTT  Bolzen gebrochen. Bolzen neu angefertig und di...   
5      Reparatur UTT                                 Feder ausgetauscht   
6      Reparatur UTT       Schrauben ausgebohrt Gewinde nachgeschnitten   
8      Reparatur UTT  da derzeit Keine Ersatzteile da Reparatur mit ...   

  MPMelderArbeitsplatz MPAbteilungBezeichnung Arbeitsbeginn ErstellungsDatum  
3              Weberei                Weberei    2019-03-21       2019-03-21  
4              Vorwerk                Vorwerk    2019-03-25       2019-03-25  
5           Warenschau             Warenschau    2019-03-25       2019-03-25  
6              Vorwerk                Vorwerk    2019-03-25       2019-03-22  
8              Weberei                Weberei    2019-04-02       2019-04-01

In [75]:
descriptions = base[feature]
print(f"Einträge: {len(descriptions)}")

Einträge: 118086


In [76]:
num_dupl_descr = descriptions.duplicated().sum()
uni_descr = descriptions.unique()
num_uni_descr = len(uni_descr)

print(f"Anzahl Duplikate {feature}: {num_dupl_descr}")
print(f"Anzahl einzigartiger {feature}: {num_uni_descr}")
print(f"Anteil einzigartiger {feature}: {num_uni_descr / len(descriptions) * 100:.2f} %")

Anzahl Duplikate ErledigungsBeschreibung: 110707
Anzahl einzigartiger ErledigungsBeschreibung: 7379
Anteil einzigartiger ErledigungsBeschreibung: 6.25 %


In [77]:
LOAD_CALC_FILES

False

In [78]:
if not LOAD_CALC_FILES:
    cols = ['descr', 'len', 'num_occur', 'assoc_obj_ids', 'num_assoc_obj_ids']
    descr_df = pd.DataFrame(columns=cols)
    max_val = 0
    text = None
    index = 0


    for idx, description in enumerate(uni_descr):
        len_descr = len(description)
        filt = base[feature] == description
        temp = base[filt]
        assoc_obj_ids = temp['ObjektID'].unique()
        assoc_obj_ids = np.sort(assoc_obj_ids, kind='stable')
        num_assoc_obj_ids = len(assoc_obj_ids)
        num_dupl = filt.sum()
        
        conc_df = pd.DataFrame(data=[[
                                description,
                                len_descr,
                                num_dupl,
                                assoc_obj_ids,
                                num_assoc_obj_ids
                            ]], columns=cols)
        
        descr_df = pd.concat([descr_df, conc_df], ignore_index=True)
        
        if num_dupl > max_val:
            max_val = num_dupl
            index = idx
            text = description
            
    temp1 = descr_df.sort_values(by='num_occur', ascending=False)

In [79]:
temp1

descr  len num_occur  \
112   Sichtkontrolle durchgeführt Auffälligkeiten fe...   95     98720   
108   Sichtkontrolle durchgeführt Auffälligkeiten fe...  100      1450   
147   Externe Prüfung wurde durchgeführt Beanstandun...  119      1082   
128   Reinigung durchgeführt Auffälligkeiten festges...   90       762   
96    Sichtkontrolle wie festgelegt durchgeführt Auf...  110       648   
...                                                 ...  ...       ...   
2805  X Achse Süd Führungswägen Kurze Version eingebaut   49         1   
2804  Maschinenrahmen ausgerichtet und ausgebeult. M...   90         1   
2803                     Bügel und Stützräder getauscht   30         1   
2802   Graf: TK wurde in Arbeitsauftrag 65487 gewandelt   48         1   
7378                            Neue Gasfeder eingebaut   23         1   

                                          assoc_obj_ids num_assoc_obj_ids  
112   [0, 1, 7, 17, 41, 42, 43, 44, 45, 46, 47, 51, ...               953  
108   [0, 1, 140, 301, 305, 313, 314, 576, 970, 1110...                28  
147   [191, 193, 195, 197, 200, 264, 287, 288, 289, ...               413  
128   [0, 1, 7, 123, 136, 137, 138, 177, 298, 304, 3...                90  
96    [1, 20, 21, 51, 52, 53, 54, 55, 56, 64, 65, 66...               271  
...                                                 ...               ...  
2805                                               [21]                 1  
2804                                              [144]                 1  
2803                                              [315]                 1  
2802                                              [405]                 1  
7378                                              [326]                 1  

[7379 rows x 5 columns]

In [81]:
temp1.iat[0,0]

'Sichtkontrolle durchgeführt Auffälligkeiten festgestellt vom Ausführenden bitte dazu schreiben:'

In [82]:
temp1.iat[1,0]

'Sichtkontrolle durchgeführt Auffälligkeiten festgestellt vom Ausführenden bitte dazu schreiben: Nein'

In [83]:
# save/load dataframe
FILE_PATH = f'{feature}_analyse_1.fth'
if LOAD_CALC_FILES:
    temp1 = pd.read_feather(FILE_PATH)
    temp1 = temp1.set_index('index')
else:
    save_df = temp1.reset_index()
    save_df.to_feather(FILE_PATH)

#### Gesamter Datensatz

In [84]:
# analysiere erste 10 Einträge
descr = temp1[['descr', 'num_occur']]
#descr = descr.iloc[50:200,:]

In [85]:
#descr.iat[0,0] = 'Das ist ein Test am 24.08.2023'

In [86]:
len(descr)

7379

In [87]:
descr

descr num_occur
112   Sichtkontrolle durchgeführt Auffälligkeiten fe...     98720
108   Sichtkontrolle durchgeführt Auffälligkeiten fe...      1450
147   Externe Prüfung wurde durchgeführt Beanstandun...      1082
128   Reinigung durchgeführt Auffälligkeiten festges...       762
96    Sichtkontrolle wie festgelegt durchgeführt Auf...       648
...                                                 ...       ...
2805  X Achse Süd Führungswägen Kurze Version eingebaut         1
2804  Maschinenrahmen ausgerichtet und ausgebeult. M...         1
2803                     Bügel und Stützräder getauscht         1
2802   Graf: TK wurde in Arbeitsauftrag 65487 gewandelt         1
7378                            Neue Gasfeder eingebaut         1

[7379 rows x 2 columns]

In [88]:
#LOAD_CALC_FILES = True
#LOAD_CALC_FILES = False
#IS_TEST = True
IS_TEST = False

In [89]:
# adjacency matrix
connections = dict()
unique_tokens = set()
UPDATE_STATUS = 500
length_data = len(descr)
spell_check_candidates = set()
spell_checker = SpellChecker(language='de', distance=1)

if not LOAD_CALC_FILES or IS_TEST:
    for count, description in enumerate(descr.iterrows()):
        
        text = description[1]['descr']
        weight = description[1]['num_occur']
        
        doc = nlp(text)
        
        obtain_descendant_info(
            doc=doc,
            weight=weight,
            POS_of_interest=POS_of_interest,
            TAG_of_interest=TAG_of_interest,
            connections=connections,
            unique_tokens=unique_tokens,
            spell_check_candidates=spell_check_candidates,
            spell_check_whitelist=spell_check_whitelist,
            spell_checker=spell_checker,
            corrections=corrections,
        )
        
        if count % UPDATE_STATUS == 0:
            logger.info(f'Number of entries processed: {count+1}, Percent completed: {((count+1) / length_data) * 100:.2f}')

INFO:base:Number of entries processed: 1, Percent completed: 0.01
INFO:base:Number of entries processed: 501, Percent completed: 6.79
INFO:base:Number of entries processed: 1001, Percent completed: 13.57
INFO:base:Number of entries processed: 1501, Percent completed: 20.34
INFO:base:Number of entries processed: 2001, Percent completed: 27.12
INFO:base:Number of entries processed: 2501, Percent completed: 33.89
INFO:base:Number of entries processed: 3001, Percent completed: 40.67
INFO:base:Number of entries processed: 3501, Percent completed: 47.45
INFO:base:Number of entries processed: 4001, Percent completed: 54.22
INFO:base:Number of entries processed: 4501, Percent completed: 61.00
INFO:base:Number of entries processed: 5001, Percent completed: 67.77
INFO:base:Number of entries processed: 5501, Percent completed: 74.55
INFO:base:Number of entries processed: 6001, Percent completed: 81.33
INFO:base:Number of entries processed: 6501, Percent completed: 88.10
INFO:base:Number of entrie

In [93]:
ADJ_DF_PATH = f'./Graphanalyse/adj_mat_df_{feature}.fth'
if not IS_TEST:
    if LOAD_CALC_FILES:
        adj_mat_undir = pd.read_feather(ADJ_DF_PATH)
        adj_mat_undir = adj_mat_undir.set_index('index')
        # additional information
        connections = load_pickle('connections.pkl')
        unique_tokens = load_pickle('unique_tokens.pkl')
    else:
        adj_mat = obtain_adj_matrix(unique_tokens=unique_tokens, connections=connections)
        adj_mat_undir = make_undir_adj_matrix(adj_mat=adj_mat)
        save_df = adj_mat_undir.reset_index()
        save_df.to_feather(ADJ_DF_PATH)
        # additional information
        save_pickle(obj=connections, path='connections.pkl')
        save_pickle(obj=unique_tokens, path='unique_tokens.pkl')

In [94]:
adj_mat_undir.sort_index()

funktionsfähig  Zwischenbehälter  Ölfilter  Rechter  \
-20C                                0                 0         0        0   
-Befestihgung                       0                 0         0        0   
-Einlaufwalze                       0                 0         0        0   
-Entlüftungssicherung               0                 0         0        0   
-Faltbalken                         0                 0         0        0   
...                               ...               ...       ...      ...   
überzogenn                          0                 0         0        0   
überzoggen                          0                 0         0        0   
übrtprüfen                          0                 0         0        0   
ünerziehen                          0                 0         0        0   
üperprüfen                          0                 0         0        0   

                       Kontaktproblem  Geschweisst  vorbereiten  Gelenkbolzen  \
-20C                                0            0            0             0   
-Befestihgung                       0            0            0             0   
-Einlaufwalze                       0            0            0             0   
-Entlüftungssicherung               0            0            0             0   
-Faltbalken                         0            0            0             0   
...                               ...          ...          ...           ...   
überzogenn                          0            0            0             0   
überzoggen                          0            0            0             0   
übrtprüfen                          0            0            0             0   
ünerziehen                          0            0            0             0   
üperprüfen                          0            0            0             0   

                       Silikonfass  Ausbau  ...  Kom  anlernen  nah  \
-20C                             0       0  ...    0         0    0   
-Befestihgung                    0       0  ...    0         0    0   
-Einlaufwalze                    0       0  ...    0         0    0   
-Entlüftungssicherung            0       0  ...    0         0    0   
-Faltbalken                      0       0  ...    0         0    0   
...                            ...     ...  ...  ...       ...  ...   
überzogenn                       0       0  ...    0         0    0   
überzoggen                       0       0  ...    0         0    0   
übrtprüfen                       0       0  ...    0         0    0   
ünerziehen                       0       0  ...    0         0    0   
üperprüfen                       0       0  ...    0         0    0   

                       Begutachtung  Betriebszeit  paletten  augetreten  \
-20C                              0             0         0           0   
-Befestihgung                     0             0         0           0   
-Einlaufwalze                     0             0         0           0   
-Entlüftungssicherung             0             0         0           0   
-Faltbalken                       0             0         0           0   
...                             ...           ...       ...         ...   
überzogenn                        0             0         0           0   
überzoggen                        0             0         0           0   
übrtprüfen                        0             0         0           0   
ünerziehen                        0             0         0           0   
üperprüfen                        0             0         0           0   

                       Antriebszahnrad  Gewindereparaturset  Heizventil  
-20C                                 0                    0           0  
-Befestihgung                        0                    0           0  
-Einlaufwalze                        0                    0           0  
-Entlüftungssicherung                0                    0    

In [95]:
arr = adj_mat_undir.to_numpy()

In [96]:
np.count_nonzero(arr)

24171

In [97]:
np.max(arr)

103601

Threshold

In [110]:
WEIGHT_THRESHOLD = 30

In [111]:
arr = adj_mat_undir.to_numpy()

In [112]:
arr = np.where(arr < WEIGHT_THRESHOLD, 0, arr)

In [113]:
np.count_nonzero(arr)

138

In [116]:
thresh_adj_mat = adj_mat_undir.copy()
thresh_adj_mat.loc[:] = arr

In [117]:
thresh_adj_mat

funktionsfähig  Zwischenbehälter  Ölfilter  Rechter  \
funktionsfähig                    0                 0         0        0   
Zwischenbehälter                  0                 0         0        0   
Ölfilter                          0                 0         0        0   
Rechter                           0                 0         0        0   
Kontaktproblem                    0                 0         0        0   
...                             ...               ...       ...      ...   
paletten                          0                 0         0        0   
augetreten                        0                 0         0        0   
Antriebszahnrad                   0                 0         0        0   
Gewindereparaturset               0                 0         0        0   
Heizventil                        0                 0         0        0   

                     Kontaktproblem  Geschweisst  vorbereiten  Gelenkbolzen  \
funktionsfähig                    0            0            0             0   
Zwischenbehälter                  0            0            0             0   
Ölfilter                          0            0            0             0   
Rechter                           0            0            0             0   
Kontaktproblem                    0            0            0             0   
...                             ...          ...          ...           ...   
paletten                          0            0            0             0   
augetreten                        0            0            0             0   
Antriebszahnrad                   0            0            0             0   
Gewindereparaturset               0            0            0             0   
Heizventil                        0            0            0             0   

                     Silikonfass  Ausbau  ...  Kom  anlernen  nah  \
funktionsfähig                 0       0  ...    0         0    0   
Zwischenbehälter               0       0  ...    0         0    0   
Ölfilter                       0       0  ...    0         0    0   
Rechter                        0       0  ...    0         0    0   
Kontaktproblem                 0       0  ...    0         0    0   
...                          ...     ...  ...  ...       ...  ...   
paletten                       0       0  ...    0         0    0   
augetreten                     0       0  ...    0         0    0   
Antriebszahnrad                0       0  ...    0         0    0   
Gewindereparaturset            0       0  ...    0         0    0   
Heizventil                     0       0  ...    0         0    0   

                     Begutachtung  Betriebszeit  paletten  augetreten  \
funktionsfähig                  0             0         0           0   
Zwischenbehälter                0             0         0           0   
Ölfilter                        0             0         0           0   
Rechter                         0             0         0           0   
Kontaktproblem                  0             0         0           0   
...                           ...           ...       ...         ...   
paletten                        0             0         0           0   
augetreten                      0             0         0           0   
Antriebszahnrad                 0             0         0           0   
Gewindereparaturset             0             0         0           0   
Heizventil                      0             0         0           0   

                     Antriebszahnrad  Gewindereparaturset  Heizventil  
funktionsfähig                     0                    0           0  
Zwischenbehälter                   0                    0           0  
Ölfilter                           0                    0           0  
Rechter                            0                    0           0  
Kontaktproblem                     0                    0           0  
...                  

In [118]:
ADJ_MAT_PATH_CSV = f'./Graphanalyse/adj_mat_thresh_{feature}_{WEIGHT_THRESHOLD}.csv'
thresh_adj_mat.to_csv(path_or_buf=ADJ_MAT_PATH_CSV, encoding='cp1252', sep=';')

---
# **Zusatz**

#### **Analysiere beispielhaft Eintrag mit meisten Duplikaten**

In [64]:
crit = uni_descr[171]
filt = wo_duplicates['VorgangsBeschreibung'] == crit
temp = wo_duplicates[filt]
print(f"Anzahl Einträge mit gewählter Beschreibung: {len(temp)}")

Anzahl Einträge mit gewählter Beschreibung: 47689


In [65]:
temp.head()

VorgangsID  ObjektID                                      HObjektText  \
288      155717       187                      246, Webmaschine Jacquard,    
289      152507       177   204 S SI , Webmaschine, DL 280 EMS Breite 220    
318      255972       249  203 C S SI, Webmaschine, DL 280 EMS Breite 220    
319      255977       249  203 C S SI, Webmaschine, DL 280 EMS Breite 220    
340      267942       187                      246, Webmaschine Jacquard,    

     ObjektArtID         ObjektArtText  VorgangsTypID VorgangsTypName  \
288            6  Jacquard-Webmaschine              1         Wartung   
289            3      Luft-Webmaschine              1         Wartung   
318            3      Luft-Webmaschine              1         Wartung   
319            3      Luft-Webmaschine              1         Wartung   
340            6  Jacquard-Webmaschine              1         Wartung   

    VorgangsDatum  VorgangsStatusId  VorgangsPrioritaet  \
288    2022-04-01                 5                   0   
289    2022-04-09                 5                   0   
318    2022-07-30                 5                   0   
319    2022-08-04                 5                   0   
340    2022-08-07                 5                   0   

                                  VorgangsBeschreibung VorgangsOrt  \
288  Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   
289  Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   
318  Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   
319  Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   
340  Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   

                                  VorgangsArtText ErledigungsDatum  \
288  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
289  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-09   
318  Tägliche Interne Wartungstätigkeiten Weberei       2022-07-30   
319  Tägliche Interne Wartungstätigkeiten Weberei       2022-08-04   
340  Tägliche Interne Wartungstätigkeiten Weberei       2022-08-07   

              ErledigungsArtText  \
288  Intern UTT - Sichtkontrolle   
289  Intern UTT - Sichtkontrolle   
318  Intern UTT - Sichtkontrolle   
319  Intern UTT - Sichtkontrolle   
340  Intern UTT - Sichtkontrolle   

                               ErledigungsBeschreibung MPMelderArbeitsplatz  \
288  Sichtkontrolle durchgeführt\n\nAuffälligkeiten...                  NaN   
289  Sichtkontrolle durchgeführt\n\nAuffälligkeiten...                  NaN   
318  Sichtkontrolle durchgeführt\n\nAuffälligkeiten...                  NaN   
319  Sichtkontrolle durchgeführt\n\nAuffälligkeiten...                  NaN   
340  Sichtkontrolle durchgeführt\n\nAuffälligkeiten...                  NaN   

    MPAbteilungBezeichnung Arbeitsbeginn ErstellungsDatum  
288                    NaN    2022-04-01       2022-02-17  
289                    NaN    2022-04-09       2022-02-17  
318                    NaN    2022-07-30       2022-04-28  
319                    NaN    2022-08-04       2022-04-28  
340                    NaN    2022-08-07       2022-08-05

In [66]:
# schaue welche Merkmale abweichend sind
analyse_columns = ['ObjektID', 'VorgangsTypID', 'VorgangsTypName']

ObjektID

In [67]:
temp['ObjektID'].unique()

array([ 187,  177,  249, 2654, 1792,  272,  271,  270,  269,  268,  186,
        178,  179, 2317, 2318, 2473, 2559, 1244,  240,  241,  180,  220,
        221,  222,  223,  224,  961,  962, 2166, 3212,  267,  266,  181,
        182,  213,  214,  174,  175,  176,  156,  157,  158,  247,  248,
        183,  265,  278, 1793, 1794,  218,  217,  219,  215,  216, 2319,
       2320,  228,  184,  152,  153, 2165,  154,  155,  159,  167,  168,
        169, 2313, 2314, 2315, 2316,  212,  211,  160,  161,  162,  164,
        165,  166,  264,  273,  274,  277,  276,  275,  279,  280,  281,
        282,  283,  242,  243,  244,  245,  246,  225,  227,  229,  170,
        171,  172,  173,  230,  231, 3213, 3211, 3214], dtype=int64)

In [68]:
filt = temp['ObjektID'] == 2318
temp_fil1 = temp[filt]

In [69]:
temp_fil1.head()

VorgangsID  ObjektID                                HObjektText  \
878        269743      2318  A067, Webmaschine, DL 280 EMS Breite 280    
6099       152490      2318  A067, Webmaschine, DL 280 EMS Breite 280    
13905      152476      2318  A067, Webmaschine, DL 280 EMS Breite 280    
14019      248301      2318  A067, Webmaschine, DL 280 EMS Breite 280    
14211      254914      2318  A067, Webmaschine, DL 280 EMS Breite 280    

       ObjektArtID     ObjektArtText  VorgangsTypID VorgangsTypName  \
878              3  Luft-Webmaschine              1         Wartung   
6099             3  Luft-Webmaschine              1         Wartung   
13905            3  Luft-Webmaschine              1         Wartung   
14019            3  Luft-Webmaschine              1         Wartung   
14211            3  Luft-Webmaschine              1         Wartung   

      VorgangsDatum  VorgangsStatusId  VorgangsPrioritaet  \
878      2022-10-31                 5                   0   
6099     2022-03-24                 5                   0   
13905    2022-03-10                 5                   0   
14019    2022-04-28                 5                   0   
14211    2022-05-19                 5                   0   

                                    VorgangsBeschreibung VorgangsOrt  \
878    Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   
6099   Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   
13905  Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   
14019  Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   
14211  Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   

                                    VorgangsArtText ErledigungsDatum  \
878    Tägliche Interne Wartungstätigkeiten Weberei       2022-10-31   
6099   Tägliche Interne Wartungstätigkeiten Weberei       2022-03-24   
13905  Tägliche Interne Wartungstätigkeiten Weberei       2022-03-10   
14019  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-28   
14211  Tägliche Interne Wartungstätigkeiten Weberei       2022-05-19   

                ErledigungsArtText  \
878    Intern UTT - Sichtkontrolle   
6099   Intern UTT - Sichtkontrolle   
13905  Intern UTT - Sichtkontrolle   
14019  Intern UTT - Sichtkontrolle   
14211  Intern UTT - Sichtkontrolle   

                                 ErledigungsBeschreibung MPMelderArbeitsplatz  \
878    Sichtkontrolle durchgeführt\n\nAuffälligkeiten...                  NaN   
6099   Sichtkontrolle durchgeführt\n\nAuffälligkeiten...                  NaN   
13905  Sichtkontrolle durchgeführt\n\nAuffälligkeiten...                  NaN   
14019  Sichtkontrolle durchgeführt\n\nAuffälligkeiten...                  NaN   
14211  Sichtkontrolle durchgeführt\n\nAuffälligkeiten...                  NaN   

      MPAbteilungBezeichnung Arbeitsbeginn ErstellungsDatum  
878                      NaN    2022-10-31       2022-08-05  
6099                     NaN    2022-03-24       2022-02-17  
13905                    NaN    2022-03-10       2022-02-17  
14019                    NaN    2022-04-28       2022-04-14  
14211                    NaN    2022-05-19       2022-04-28

In [70]:
temp_fil1['VorgangsDatum'].unique()

<DatetimeArray>
['2022-10-31 00:00:00', '2022-03-24 00:00:00', '2022-03-10 00:00:00',
 '2022-04-28 00:00:00', '2022-05-19 00:00:00', '2022-04-09 00:00:00',
 '2022-04-21 00:00:00', '2022-06-11 00:00:00', '2022-05-12 00:00:00',
 '2022-04-23 00:00:00',
 ...
 '2022-10-28 00:00:00', '2022-07-06 00:00:00', '2023-06-14 00:00:00',
 '2022-10-29 00:00:00', '2022-07-07 00:00:00', '2023-06-15 00:00:00',
 '2022-05-05 00:00:00', '2022-10-30 00:00:00', '2022-07-08 00:00:00',
 '2022-10-19 00:00:00']
Length: 462, dtype: datetime64[ns]

In [71]:
len(temp_fil1)

462

VorgangsID

In [ ]:
uni_VorgangsID = temp['VorgangsID'].unique()
num_uni_VorgangsID = len(uni_VorgangsID)
print(f'Anzahl einzigartiger VorgangsID {num_uni_VorgangsID} mit Anteil am Gesamtdatensatz {num_uni_VorgangsID / len(temp) * 100:.2f} %')

Anzahl einzigartiger VorgangsID 1855 mit Anteil am Gesamtdatensatz 3.89 %


In [ ]:
uni_VorgangsID[0]

155717

In [50]:
filt = temp['VorgangsID'] == uni_VorgangsID[0]
temp_fil1 = temp[filt]

In [51]:
temp_fil1

VorgangsID  ObjektID                    HObjektText  ObjektArtID  \
288       155717       187    246, Webmaschine Jacquard,             6   
2718      155717      1792   A057, Webmaschine Jacquard,             6   
2719      155717       186  245 J, Webmaschine Jacquard,             6   
2720      155717      2473   A056, Webmaschine Jacquard,             6   
5504      155717      2559   A070, Webmaschine Jacquard,             6   
5505      155717       961   A054, Webmaschine Jacquard,             6   
5506      155717       962   A055, Webmaschine Jacquard,             6   
5507      155717      2166   A061, Webmaschine Jacquard,             6   
5508      155717      1793   A058, Webmaschine Jacquard,             6   
5509      155717      1794   A059, Webmaschine Jacquard,             6   
8294      155717      2165   A060, Webmaschine Jacquard,             6   

             ObjektArtText  VorgangsTypID VorgangsTypName VorgangsDatum  \
288   Jacquard-Webmaschine              1         Wartung    2022-04-01   
2718  Jacquard-Webmaschine              1         Wartung    2022-04-01   
2719  Jacquard-Webmaschine              1         Wartung    2022-04-01   
2720  Jacquard-Webmaschine              1         Wartung    2022-04-01   
5504  Jacquard-Webmaschine              1         Wartung    2022-04-01   
5505  Jacquard-Webmaschine              1         Wartung    2022-04-01   
5506  Jacquard-Webmaschine              1         Wartung    2022-04-01   
5507  Jacquard-Webmaschine              1         Wartung    2022-04-01   
5508  Jacquard-Webmaschine              1         Wartung    2022-04-01   
5509  Jacquard-Webmaschine              1         Wartung    2022-04-01   
8294  Jacquard-Webmaschine              1         Wartung    2022-04-01   

      VorgangsStatusId  VorgangsPrioritaet  \
288                  5                   0   
2718                 5                   0   
2719                 5                   0   
2720                 5                   0   
5504                 5                   0   
5505                 5                   0   
5506                 5                   0   
5507                 5                   0   
5508                 5                   0   
5509                 5                   0   
8294                 5                   0   

                                   VorgangsBeschreibung VorgangsOrt  \
288   Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   
2718  Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   
2719  Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   
2720  Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   
5504  Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   
5505  Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   
5506  Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   
5507  Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   
5508  Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   
5509  Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   
8294  Tägliche Wartungstätigkeiten nach Vorgabe des ...         NaN   

                                   VorgangsArtText ErledigungsDatum  \
288   Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
2718  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
2719  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
2720  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
5504  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
5505  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
5506  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
5507  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
5508  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
5509  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
8294  Tägliche Interne Wartun

In [63]:
temp_fil2 = temp_fil1.fillna(value=False)
print(f'Anzahl Einträge mit gewählter VorgangsID: {len(temp_fil2)}')
uni_obj_id = len(temp_fil2['ObjektID'].unique())
print(f'Anzahl einzigartiger ObjektIDs darunter: {uni_obj_id}')

Anzahl Einträge mit gewählter VorgangsID: 11
Anzahl einzigartiger ObjektIDs darunter: 11


In [72]:
temp_fil2['ObjektID'].unique()

array([ 187, 1792,  186, 2473, 2559,  961,  962, 2166, 1793, 1794, 2165],
      dtype=int64)

In [55]:
temp_fil2

VorgangsID  ObjektID                    HObjektText  ObjektArtID  \
288       155717       187    246, Webmaschine Jacquard,             6   
2718      155717      1792   A057, Webmaschine Jacquard,             6   
2719      155717       186  245 J, Webmaschine Jacquard,             6   
2720      155717      2473   A056, Webmaschine Jacquard,             6   
5504      155717      2559   A070, Webmaschine Jacquard,             6   
5505      155717       961   A054, Webmaschine Jacquard,             6   
5506      155717       962   A055, Webmaschine Jacquard,             6   
5507      155717      2166   A061, Webmaschine Jacquard,             6   
5508      155717      1793   A058, Webmaschine Jacquard,             6   
5509      155717      1794   A059, Webmaschine Jacquard,             6   
8294      155717      2165   A060, Webmaschine Jacquard,             6   

             ObjektArtText  VorgangsTypID VorgangsTypName VorgangsDatum  \
288   Jacquard-Webmaschine              1         Wartung    2022-04-01   
2718  Jacquard-Webmaschine              1         Wartung    2022-04-01   
2719  Jacquard-Webmaschine              1         Wartung    2022-04-01   
2720  Jacquard-Webmaschine              1         Wartung    2022-04-01   
5504  Jacquard-Webmaschine              1         Wartung    2022-04-01   
5505  Jacquard-Webmaschine              1         Wartung    2022-04-01   
5506  Jacquard-Webmaschine              1         Wartung    2022-04-01   
5507  Jacquard-Webmaschine              1         Wartung    2022-04-01   
5508  Jacquard-Webmaschine              1         Wartung    2022-04-01   
5509  Jacquard-Webmaschine              1         Wartung    2022-04-01   
8294  Jacquard-Webmaschine              1         Wartung    2022-04-01   

      VorgangsStatusId  VorgangsPrioritaet  \
288                  5                   0   
2718                 5                   0   
2719                 5                   0   
2720                 5                   0   
5504                 5                   0   
5505                 5                   0   
5506                 5                   0   
5507                 5                   0   
5508                 5                   0   
5509                 5                   0   
8294                 5                   0   

                                   VorgangsBeschreibung  VorgangsOrt  \
288   Tägliche Wartungstätigkeiten nach Vorgabe des ...        False   
2718  Tägliche Wartungstätigkeiten nach Vorgabe des ...        False   
2719  Tägliche Wartungstätigkeiten nach Vorgabe des ...        False   
2720  Tägliche Wartungstätigkeiten nach Vorgabe des ...        False   
5504  Tägliche Wartungstätigkeiten nach Vorgabe des ...        False   
5505  Tägliche Wartungstätigkeiten nach Vorgabe des ...        False   
5506  Tägliche Wartungstätigkeiten nach Vorgabe des ...        False   
5507  Tägliche Wartungstätigkeiten nach Vorgabe des ...        False   
5508  Tägliche Wartungstätigkeiten nach Vorgabe des ...        False   
5509  Tägliche Wartungstätigkeiten nach Vorgabe des ...        False   
8294  Tägliche Wartungstätigkeiten nach Vorgabe des ...        False   

                                   VorgangsArtText ErledigungsDatum  \
288   Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
2718  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
2719  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
2720  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
5504  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
5505  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
5506  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
5507  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
5508  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
5509  Tägliche Interne Wartungstätigkeiten Weberei       2022-04-01   
8294  Tägliche In

*Frage: Können einem Vorgang mehrere ObjektIDs zugeordnet werden? Wenn ja, warum dann unterschiedliche Erledigungsdaten?*

**Länge der Beschreibungen**

In [73]:
descriptions = descriptions.to_frame()
descriptions['length_description'] = descriptions.applymap(func=lambda x: len(x))
descriptions = descriptions.sort_values(by=['length_description'], ascending=False)

In [74]:
# stats
len_descr = descriptions['length_description']
len_descr.describe()

count    124008.000000
mean         70.351751
std          53.080901
min           1.000000
25%          66.000000
50%          66.000000
75%          67.000000
max        3137.000000
Name: length_description, dtype: float64

In [75]:
descriptions.head()

VorgangsBeschreibung  length_description
8704    Vorgaben aus Held Wartungsplan\n\nLC-X-Achse /...                3137
7826    Vorgaben aus Held Wartungsplan\n\nLC-X-Achse /...                3137
49779   Laut Wartungsvertrag (Hr.Radtke) Bestellnummer...                2311
124118  Laut Wartungsvertrag (Hr.Radtke) Bestellnummer...                2311
14853   Laut Wartungsvertrag (Hr.Radtke) Bestellnummer...                2311

In [76]:
descriptions

VorgangsBeschreibung  length_description
8704    Vorgaben aus Held Wartungsplan\n\nLC-X-Achse /...                3137
7826    Vorgaben aus Held Wartungsplan\n\nLC-X-Achse /...                3137
49779   Laut Wartungsvertrag (Hr.Radtke) Bestellnummer...                2311
124118  Laut Wartungsvertrag (Hr.Radtke) Bestellnummer...                2311
14853   Laut Wartungsvertrag (Hr.Radtke) Bestellnummer...                2311
...                                                   ...                 ...
13450                                                                       1
13451                                                                       1
29979                                                                       1
13452                                                                       1
21214                                                  \n                   1

[124008 rows x 2 columns]